## Parcel Update - Fall 2018
#### By Mason Bindl

### Get Parcel Data

#### El Dorado County Data:
#### http://gem.edcgov.us/gotnetextracts/

#### Placer County Data:
#### email: KBerger@placer.ca.gov

#### Washoe County Data:
#### http://explore-washoe.opendata.arcgis.com/

#### Carson City County Data:
#### http://data-carsoncity.opendata.arcgis.com/datasets/parcels

#### Douglas County Data:
#### email: mrichardson@douglasnv.us phone: 775-782-9894

### Import modules and Set local variables

In [6]:
import arcpy, sys, datetime, os, traceback
# Set Data Source GDB Names
county_gdb = "Original.gdb"
TRPA_staging_gdb = "Staging.gdb"
w_folder = '2018_10'  # Change based on new file folder name
w_original = '\\Original\\'
w_modified = '\\Modified\\'
n_parcels = 'Parcels'
sep = '-'
County_List = ['Carson', 'Douglas', 'El_Dorado', 'Placer', 'Washoe']
County_ABR_List = ['CC', 'DG', 'EL', 'PL', 'WA']
state_loc = ['CA', 'NV']
python_version = "PYTHON3"

# set base feature classes
ParcelLayer = "C:\\GIS\\PROJECT\\2018_10\\Workspace\\ParcelUpdate_Workspace.gdb\\Parcel_Master_1"
ParcelPoint = "C:\\GIS\\PROJECT\\2018_10\\Workspace\\ParcelUpdate_Workspace.gdb\\Parcel_Point"

if arcpy.Exists(ParcelPoint):
    arcpy.Delete_management(ParcelPoint)
arcpy.FeatureToPoint_management(ParcelLayer, ParcelPoint, "INSIDE")

# SDE feature classes from C: drive
# sde_FireDistrict = "C:\\GIS\\PROJECT\\SDE\\SDE_Archive_2018.gdb\\Jurisdictions\\FireDistricts"

# File paths
sdeBase = "F:\\GIS\\GIS_DATA\\Vector.sde"
#sde feature classes
sde_FireDistrict = sdeBase + "\\sde.SDE.Jurisdictions\\sde.SDE.FireDistricts"
sde_NRCSSoils1974 = sdeBase + "\\sde.SDE.Soils\\sde.SDE.NRCS_Soils_1974"
sde_NRCSSoils2003 = sdeBase + "\\sde.SDE.Soils\\sde.SDE.NRCS_Soils_2003"
sde_HydroArea = sdeBase + "\\sde.SDE.Water\\sde.SDE.Hydro_Areas"
sde_Watershed = sdeBase + "\\sde.SDE.Water\\sde.SDE.Priority"
sde_RegionalLandUse = sdeBase + "\\sde.SDE.Planning\\sde.SDE.RegionalLandUse"
sde_LocalPlan = sdeBase + "\\sde.SDE.Planning\\sde.SDE.LocalPlan"
sde_Zoning =  sdeBase + "\\sde.SDE.Planning\\sde.SDE.Zoning_LocalPlan"
sde_SpecialDistrict = sdeBase + "\\sde.SDE.Planning\\sde.SDE.SpecialPlanningDistrict"
sde_TownCenter = sdeBase + "\\sde.SDE.Planning\\sde.SDE.TownCenter"
sde_TownCenterBuffer = sdeBase + "\\sde.SDE.Planning\\sde.SDE.TownCenter_Buffer"
sde_Index1987 = sdeBase + "\\sde.SDE.Planning\\sde.SDE.AssessorMapIndex_1987"
sde_TRPAboundary = sdeBase + "\\sde.SDE.Jurisdictions\\sde.SDE.TRPA_bdy"
sde_UrbanArea = sdeBase + "\\sde.SDE.Jurisdictions\\sde.SDE.UrbanAreas"
sde_Zip = sdeBase + "\\sde.SDE.Census\\sde.SDE.Tahoe_Census_Zip"

# in memory files
wk_memory = "in_memory" + "\\"
ParcelPoint_FireDistrict = wk_memory + "ParcelPoint_FireDistrict"
ParcelPoint_Soils74 = wk_memory + "\\ParcelPoint_Soils74"
ParcelPoint_Soils03 = wk_memory + "\\ParcelPoint_Soils03"
ParcelPoint_HydroArea = wk_memory + "\\ParcelPoint_HydroArea"
ParcelPoint_Watershed = wk_memory + "\\ParcelPoint_Watershed"
ParcelPoint_RegionalLandUse = wk_memory + "\\ParcelPoint_RegionalLandUse"
ParcelPoint_LocalPlan = wk_memory + "\\ParcelPoint_LocalPlan"
ParcelPoint_TownCenter = wk_memory + "\\ParcelPoint_TownCenter"
ParcelPoint_TownCenterBuffer = wk_memory + "\\ParcelPoint_TownCenterBuffer"
ParcelPoint_Zoning = wk_memory + "\\ParcelPoint_Zoning"
ParcelPoint_SpecialDistrict = wk_memory + "\\ParcelPoint_SpecialDistrict"
ParcelPoint_Index1987 = wk_memory + "\\ParcelPoint_Index1987"
ParcelPoint_PstlTown = wk_memory + "\\ParcelPoint_PstlTown"
ParcelPoint_PstlZip = wk_memory + "\\ParcelPoint_PstlZip"

### Select County to be proccessed to set field list

In [7]:
while True:
    try:
        UserCountyResponse = input("Enter a County Name: ")
        if UserCountyResponse.lower() == "carson":
            UserCountyResponse = (County_List[0])
            County_ABR = (County_ABR_List[0])
            fld_list = ['APN', 'APN', 'Legal_Owner', 'Mail_Addr', 'Mail2_Addr', 'MCity', 'MZip', 'Land_Value',
                        'Improv_Val', 'Loc1', 'Unit', 'Dir', 'Phy_Addr', 'UPDATED', 'LU']
            break
        elif UserCountyResponse.lower() == "douglas":
            UserCountyResponse = (County_List[1])
            County_ABR = (County_ABR_List[1])
            fld_list = ['TAG', 'PPNO', 'PANAME', 'PMADD2', 'PMADD1', 'PMCTST', 'PZIP', 'YLANDV',
                        'YIMPRV', 'PLOC_', 'PLOCU_', 'PLOCDR', 'PLOCNM', 'PUPDDT', 'YLDUSE', 'PLOCTP', 'PAPPYR', 'PTOWN',
                        'POLDP_', 'POLDDT']
            break
        elif UserCountyResponse.lower() == "el_dorado" or UserCountyResponse.lower() == "el dorado":
            UserCountyResponse = (County_List[2])
            County_ABR = (County_ABR_List[2])
            fld_list = ['PRCL_ID', 'PRCL_ID', 'OWNER_NAME', 'OWNER_ADDR', 'OWNER_CITY', 'OWNER_STAT', 'OWNER_ZIP',
                        'LANDVAL', 'STRUCVAL', 'SITUSNUMBR', 'UNIT_NBR', 'SITUSSTRNM', 'SITUSSTRTY', 'POLY_CREAT',
                        'USECDPRI', 'CITY', 'LANDVAL', 'STRUCVAL']
            break
        elif UserCountyResponse.lower() == "placer":
            UserCountyResponse = (County_List[3])
            County_ABR = (County_ABR_List[3])
            fld_list = ['APN', 'GISAPN', 'OWNER1', 'ADR1', 'ADR2', 'CITY', 'STATE', 'ZIP', 'LANDVALUE', 'STRUCTURE',
                        'STREETNUM', 'SP_APT', 'STREETDIR', 'STREETNAME', 'STREETTYPE', 'USE_CD', 'COMMUNITY', 'TAXYEAR', 'TRANSACTIO']
            break
        elif UserCountyResponse.lower() == "washoe":
            UserCountyResponse = (County_List[4])
            County_ABR = (County_ABR_List[4])
            fld_list = ['PIN', 'APN', 'FIRSTNAME', 'LASTNAME', 'MAILING1', 'MAILING2', 'MAILCITY', 'MAILSTATE',
                        'MAILZIP', 'LANDASS', 'BUILDASS',
                        'STREETNUM', 'STREETDIR', 'STREET', 'LAND_USE', 'TAXYEAR', 'CITY', 'SITUSZIP']
            break
        else:
            print ("County entered is not valid. Try a county listed below")
            for x in County_List:
                print (x)
            print('\n')
            continue
    except Exception as e:
        print (e)
        sys.exit()
print ("{} County will be processed".format(UserCountyResponse))

Enter a County Name: El Dorado
El_Dorado County will be processed


#### Set Workspace Enviroment

In [8]:
base_working_folder = os.path.join(r'F:\GIS\ParcelUpdate', w_folder, UserCountyResponse)
arcpy.env.workspace = base_working_folder + w_original + county_gdb
print (arcpy.env.workspace)

F:\GIS\ParcelUpdate\2018_10\El_Dorado\Original\Original.gdb


#### Check for ArcInfo license

In [9]:
try:
    license_info = arcpy.ProductInfo()
    if not license_info == "NotInitialized":
        print ("Product License: {}".format(arcpy.ProductInfo()))
    else:
        raise Exception
except Exception:
    print ("ArcGIS Product License Error: {}".format(arcpy.ProductInfo()))
    sys.exit()

Product License: ArcInfo


#### Set Default Extent

In [11]:
arcpy.env.extent = sde_TRPAboundary
print ("The feature extent is being used in env {}".format(str(arcpy.env.extent)))
arcpy.env.spatialGrid1 = s_grid_1 = 5400
arcpy.env.spatialGrid2 = s_grid_2 = 16200
arcpy.env.spatialGrid3 = s_grid_3 = 48600

The feature extent is being used in env 737668.911313948 4288193.03147232 770952.921734459 4357302.88519489 NaN NaN NaN NaN


#### Set Default Coordinate System

In [12]:
arcpy.env.outputCoordinateSystem = arcpy.SpatialReference("NAD 1983 UTM Zone 10N")
sr = arcpy.env.outputCoordinateSystem
print ("Spatial Reference: {}".format(sr.name))

Spatial Reference: NAD_1983_UTM_Zone_10N


#### Remove M and Z values

In [13]:
arcpy.env.outputZFlag = "Disabled"
arcpy.env.outputMFlag = "Disabled"
arcpy.env.overwriteOutput = True

#### Set Local Variables

In [15]:
# Set local variables
out_gdb_name = County_ABR + "_" + TRPA_staging_gdb 
modified_folder = base_working_folder + w_modified
original_folder = base_working_folder + w_original
modified_fgd = modified_folder + out_gdb_name
original_fgd = original_folder + out_gdb_name
# County local variables
parcel_in_data = UserCountyResponse + '_' + n_parcels
fc_outname = parcel_in_data
fdata_name = n_parcels
fdataset = os.path.join(modified_fgd, n_parcels)
parcel_out_data = fdataset + '\\' + fc_outname
print ("Features saved here: {}".format(parcel_out_data))

Features saved here: F:\GIS\ParcelUpdate\2018_10\El_Dorado\Modified\EL_Staging.gdb\Parcels\El_Dorado_Parcels


#### Track Progress

In [36]:
# Start timer for process
start_time = datetime.datetime.today()
print ("Script started: {}".format(start_time))
# Create  and open log file.
complete_txt_path = os.path.join(base_working_folder, fc_outname + ".txt")
print (complete_txt_path)
log = open(complete_txt_path, "w")
# Write results to txt file
log.write("Log: " + str(start_time) + "\n")
log.write("\n")
log.write("Begin process:\n")
log.write("Process started at: " + str(start_time) + "\n")
log.write("\n")

Script started: 2018-11-07 12:01:47.685930
F:\GIS\ParcelUpdate\2018_10\El_Dorado\El_Dorado_Parcels.txt


1

#### Describe original feature class and its spatial reference

In [37]:
desc = arcpy.Describe(parcel_in_data)
spatialref = desc.spatialReference
print ("Original Spatial Reference: {}".format(spatialref.name))
log.write("Original Spatial Reference: {}".format(spatialref.name) + "\n")

Original Spatial Reference: NAD_1983_StatePlane_California_II_FIPS_0402_Feet


77

#### Create File GDB and Feature Class for Chosen County

In [38]:
while True:
    try:
        CreateGDBResponse = input("Create new GDB and Feature Class? (Yes/No)")
        if CreateGDBResponse.lower() == "yes":
            # Check if FileGDB exists. If not Execute CreateFileGDB
            if not arcpy.Exists(modified_fgd):
                arcpy.CreateFileGDB_management(modified_folder, out_gdb_name)
                print ("File Geodatabase {} created!".format(out_gdb_name))
                log.write("File Geodatabase {} created!".format(out_gdb_name) + "\n")
            # Execute CreateFileGDB will not be run
            else:
                print ("File Geodatabase {} already exists!".format(out_gdb_name))
                log.write("File Geodatabase {} already exists!".format(out_gdb_name) + "\n")
            # Check if Feature Dataset exists. Execute Copy
            if not arcpy.Exists(fdataset):
                arcpy.CreateFeatureDataset_management(modified_fgd, fdata_name, sr)
                print ("Feature Dataset Created!")
            # Execute Delete Management then execute CopyFeatures Management
            else:
                print ("Feature Dataset {} already exists!".format(fdata_name))
                arcpy.Delete_management(fdataset)
                print ("Deleted {}!".format(fdata_name))
                log.write("Deleted {}".format(fdata_name) + "\n")
                arcpy.CreateFeatureDataset_management(modified_fgd, fdata_name, sr)
                print ("Created Dataset {}".format(fdata_name))
            fcs = arcpy.ListFeatureClasses()
            for fc in fcs:
                # Copy features from the workspace to FGD
                arcpy.CopyFeatures_management(fc, parcel_out_data)
                print ("Added {}".format(fc))
                log.write("Added {}".format(fc) + "\n")
                # Execute GP tool to get count of records in FeatureClass
                result = arcpy.GetCount_management(parcel_out_data)
                oldresult = arcpy.GetCount_management(parcel_in_data)
                oldcount = int(oldresult.getOutput(0))
                count = int(result.getOutput(0))
                print ("Number of records copied {0} out of the {1}".format(count, oldcount))
                log.write("Number of records copied {0} out of the {1}".format(count, oldcount) + "\n")
                if count > 0:
                    # Create list of field names in FC that is being processed
                    Fc_fields = arcpy.ListFields(parcel_out_data)
                    for field in Fc_fields:
                        print ("{0} type: {1} length: {2}".format(field.name, field.type, field.length))
                        log.write("Name: {}".format(field.name) + ", ")
                        log.write("Type: {}".format(field.type) + ", ")
                        log.write("Length: {}".format(field.length) + "\n")
                    # Add all fields
                    fields = [
                        # Fields for APN & PPNO
                        ("APN_NEW", "TEXT", "", "", "16", "APN", "NULLABLE", "NON_REQUIRED", ""),
                        ("PPNO_NEW", "DOUBLE", "", "0", "", "PPNO", "NULLABLE", "NON_REQUIRED", ""),
                        # Fields for local address table
                        ("HSE_NUMBR_NEW", "SHORT", "", "", "5", "Lot #", "NULLABLE", "NON_REQUIRED", ""),
                        ("UNIT_NUMBR_NEW", "Text", "", "", "12", "Unit #", "NULLABLE", "NON_REQUIRED", ""),
                        ("STR_DIR_NEW", "Text", "", "", "2", "St Direction", "NULLABLE", "NON_REQUIRED", ""),
                        ("STR_NAME_NEW", "Text", "", "", "100", "St Name", "NULLABLE", "NON_REQUIRED", ""),
                        ("STR_SUFFIX_NEW", "Text", "", "", "6", "St Suffix", "NULLABLE", "NON_REQUIRED", ""),
                        ("APO_ADDRESS_NEW", "Text", "", "", "100", "Full Address", "NULLABLE", "NON_REQUIRED", ""),
                        ("PSTL_TOWN_NEW", "TEXT", "", "", "25", "Town", "NULLABLE", "NON_REQUIRED", ""),
                        ("PSTL_STATE_NEW", "TEXT", "", "", "2", "State", "NULLABLE", "NON_REQUIRED", ""),
                        ("PSTL_ZIP5_NEW", "TEXT", "", "", "5", "ZIP5", "NULLABLE", "NON_REQUIRED", ""),
                        # fields for mailing address
                        ("OWN_FIRST_NEW", "TEXT", "", "", "50", "Owner First Name", "NULLABLE", "NON_REQUIRED", ""),
                        ("OWN_LAST_NEW", "TEXT", "", "", "100", "Owner Last Name", "NULLABLE", "NON_REQUIRED", ""),
                        ("OWN_FULL_NEW", "TEXT", "", "", "100", "Owner Full Name", "NULLABLE", "NON_REQUIRED", ""),
                        ("MAIL_ADD1_NEW", "TEXT", "", "", "100", "Mail Address 1", "NULLABLE", "NON_REQUIRED", ""),
                        ("MAIL_ADD2_NEW", "TEXT", "", "", "100", "Mail Address 2", "NULLABLE", "NON_REQUIRED", ""),
                        ("MAIL_CITY_NEW", "TEXT", "", "", "50", "Mail City", "NULLABLE", "NON_REQUIRED", ""),
                        ("MAIL_STATE_NEW", "TEXT", "", "", "2", "Mail State", "NULLABLE", "NON_REQUIRED", ""),
                        ("MAIL_ZIP5_NEW", "TEXT", "", "", "5", "Mail ZIP5", "NULLABLE", "NON_REQUIRED", ""),
                        ("JURISDICTION_NEW", "TEXT", "", "", "4", "Jurisdiction", "NULLABLE", "NON_REQUIRED", ""),
                        ("COUNTY", "TEXT", "", "", "2", "County", "NULLABLE", "NON_REQUIRED", ""),
                        ("OWNERSHIP_TYPE", "TEXT", "", "", "12", "Ownership  Type", "NULLABLE", "NON_REQUIRED", ""),
                        ("UNITS_NEW", "SHORT", "", "", "1", "Units", "NULLABLE", "NON_REQUIRED", ""),
                        # Fields for land use, soil, watershed, etc...
                        ("COUNTY_LANDUSE", "TEXT", "", "", "4", "County Land Use", "NULLABLE", "NON_REQUIRED", ""),
                        ("COUNTY_LANDUSE_DESCRIPTION", "TEXT", "", "", "150", "County Land Use Description", "NULLABLE", "NON_REQUIRED", ""),
                        ("TRPA_LANDUSE_DESCRIPTION", "TEXT", "", "", "50", "TRPA Land Use", "NULLABLE", "NON_REQUIRED", ""),
                        ("REGIONAL_LANDUSE", "TEXT", "", "", "50", "TRPA Regional Land Use", "NULLABLE", "NON_REQUIRED", ""),
                        ("SOIL_1974", "TEXT", "", "", "5", "Soils 1974", "NULLABLE", "NON_REQUIRED", ""),
                        ("SOIL_2003", "TEXT", "", "", "5", "Soils 2003", "NULLABLE", "NON_REQUIRED", ""),
                        ("ALLOWABLE_COVERAGE_BAILEY_SQFT", "TEXT", "", "", "50", "Allowable Coverage (Bailey)", "NULLABLE", "NON_REQUIRED", ""),
                        ("IMPERVIOUS_SURFACE_SQFT", "TEXT", "", "", "50", "Impervious Surface (LiDAR, sq.ft.)", "NULLABLE", "NON_REQUIRED", ""),
                        ("HRA_NAME", "TEXT", "", "", "30", "HRA Name", "NULLABLE", "NON_REQUIRED", ""),
                        ("WATERSHED_NUMBER", "SHORT", "", "", "4", "Watershed #", "NULLABLE", "NON_REQUIRED", ""),
                        ("WATERSHED_NAME", "TEXT", "", "", "30", "Watershed Name", "NULLABLE", "NON_REQUIRED", ""),
                        ("PRIORITY_WATERSHED", "TEXT", "", "", "2", "Priority Watershed", "NULLABLE", "NON_REQUIRED", ""),
                        ("BMP_STATUS", "SHORT", "", "", "1", "BMP Status", "NULLABLE", "NON_REQUIRED", ""),
                        ("FIREPD", "TEXT", "", "", "25", "Fire Protection District", "NULLABLE", "NON_REQUIRED", ""),
                        ("WITHIN_TRPA_BNDY", "SHORT", "", "", "1", "Within TRPA Boundary", "NULLABLE", "NON_REQUIRED", ""),
                        ("LITTORAL", "SHORT", "", "", "1", "Littoral", "NULLABLE", "NON_REQUIRED", ""),
                        # Fields for Parcel Value table
                        ("AS_LANDVALUE_NEW", "LONG", "9", "", "", "Assessed Land", "NULLABLE", "NON_REQUIRED", ""),
                        ("AS_IMPROVALUE_NEW", "LONG", "9", "", "", "Assessed Improvement", "NULLABLE", "NON_REQUIRED", ""),
                        ("AS_SUM_NEW", "LONG", "9", "", "", "Assessed Sum", "NULLABLE", "NON_REQUIRED", ""),
                        ("TAX_LANDVALUE_NEW", "LONG", "9", "", "", "Tax Land", "NULLABLE", "NON_REQUIRED", ""),
                        ("TAX_IMPROVALUE_NEW", "LONG", "9", "", "", "Tax Improvement", "NULLABLE", "NON_REQUIRED", ""),
                        ("TAX_SUM_NEW", "LONG", "9", "", "", "Tax Sum", "NULLABLE", "NON_REQUIRED", ""),
                        ("TAX_YEAR_NEW", "TEXT", "", "", "4", "Tax Year", "NULLABLE", "NON_REQUIRED", ""),
                        # Fields for Planning purposes
                        ("PAS_ID", "TEXT", "", "", "8", "PAS ID", "NULLABLE", "NON_REQUIRED", ""),
                        ("PAS_NAME", "TEXT", "", "", "40", "PAS Name", "NULLABLE", "NON_REQUIRED", ""),
                        ("INDEX_1987", "TEXT", "", "", "10", "1987 Parcel Map Index", "NULLABLE", "NON_REQUIRED", ""),
                        ("INDEX_1987_HYPERLINK", "TEXT", "", "", "50", "1987 Parcel Map Index Hyperlink", "NULLABLE", "NON_REQUIRED", ""),
                        ("LOCAL_PLAN_HYPERLINK", "TEXT", "", "", "50", "Local Plan Hyperlink", "NULLABLE", "NON_REQUIRED", ""),
                        ("ZONING_NEW", "TEXT", "", "", "50", "Zoning", "NULLABLE", "NON_REQUIRED", ""),
                        ("ZONING_DESCRIPTION", "TEXT", "", "", "50", "Zoning Description", "NULLABLE", "NON_REQUIRED", ""),
                        ("SINGLE_FAMILY_DENSITY", "TEXT", "", "", "50", "Single Family Density", "NULLABLE", "NON_REQUIRED", ""),
                        ("MULTI_FAMILY_DENSITY", "TEXT", "", "", "50", "Multi-Family Density", "NULLABLE", "NON_REQUIRED", ""),
                        ("TOURIST_ACCOMMODATION_DENSITY", "TEXT", "", "", "50", "Tourist Accommodation Density", "NULLABLE", "NON_REQUIRED", ""),
                        ("BED_BREAKFAST_DENSITY", "TEXT", "", "", "50", "Bed & Breakfast Density", "NULLABLE", "NON_REQUIRED", ""),
                        ("TIME_SHARE_DENSITY", "TEXT", "", "", "50", "Time Share Density", "NULLABLE", "NON_REQUIRED", ""),
                        ("COMMERCIAL_FLOOR_AREA_ALLOWED", "TEXT", "", "", "50", "Commercial Floor Area Allowed", "NULLABLE", "NON_REQUIRED", ""),
                        ("SECONDARY_DWELLING_UNIT_ALLOWED", "TEXT", "", "", "50", "Secondary Dwelling Unit Allowed", "NULLABLE", "NON_REQUIRED", ""),
                        ("OVERLAY", "TEXT", "", "", "50", "Overlay", "NULLABLE", "NON_REQUIRED", ""),
                        ("MAX_CP_RES_DENSITY", "TEXT", "", "", "50", "Max CP RES Density", "NULLABLE", "NON_REQUIRED", ""),
                        ("MAX_CP_TAU_DENSITY", "TEXT", "", "", "50", "Max CP TAU Density", "NULLABLE", "NON_REQUIRED", ""),
                        ("SPECIAL_PLAN_AREA_OVERLAY", "TEXT", "", "", "50", "Special Pland Area Overylay", "NULLABLE", "NON_REQUIRED", ""),
                        ("TOWN_CENTER", "TEXT", "", "", "50", "Town Center", "NULLABLE", "NON_REQUIRED", ""),
                        ("SPECIAL_AREA", "TEXT", "", "", "50", "Special Area", "NULLABLE", "NON_REQUIRED", ""),
                        ("SPECIAL_PLANNING_DISTRICT", "TEXT", "", "", "50", "Special Planning District", "NULLABLE", "NON_REQUIRED", ""),
                        ("SPECIAL_PLANNING_DISTRICT_TYPE", "TEXT", "", "", "50", "Special Planning District Type", "NULLABLE", "NON_REQUIRED", ""),
                        ("LOCATION_TO_TOWNCENTER", "TEXT", "", "", "50", "Location Relative to Town Center", "NULLABLE", "NON_REQUIRED", ""),
                        ("RETIRED", "TEXT", "", "", "50", "Retired", "NULLABLE", "NON_REQUIRED", ""),
                        # Fields for Parcel Size
                        ("PARCEL_ACRES_NEW", "DOUBLE", "6", "2", "", "Acres", "NULLABLE", "NON_REQUIRED", ""),
                        ("PARCEL_SQFT_NEW", "DOUBLE", "12", "2", "", "Square Feet", "NULLABLE", "NON_REQUIRED", ""),
                        # Fields for Parcel History
                        ##("PRCL_DT_UPDATE", "Date", "", "", "", "Parcel Date Change", "NULLABLE", "NON_REQUIRED", ""),
                        ##("PREV_APN_STRD", "TEXT", "", "", "16", "Previous APN", "NULLABLE", "NON_REQUIRED", ""),
                        ##("PREV_PPNO_STRD", "DOUBLE", "11", "0", "", "Previous PPNO", "NULLABLE", "NON_REQUIRED", ""),
                        ##("APN_DT_CHANGE", "Date", "", "", "", "APN Date Change", "NULLABLE", "NON_REQUIRED", ""),
                        # Field for finding duplicates
                        ("DUPLICATE", "SHORT", "", "", "1", "", "NULLABLE", "NON_REQUIRED", "")
                    ]
                    # Create the fields using the above parameters
                    for field in fields:
                        arcpy.AddField_management(*(parcel_out_data,) + field)
                        print("{} field created".format(field))
                    break
                else:
                    print("{} No features in feature class. Exit Script".format(count))
                    exit()
            break
        elif CreateGDBResponse.lower() == "no":
            # Check if FileGDB exists.
            if arcpy.Exists(modified_fgd):
                print ("It's a go!")
                break
            else:
                print ("Staging Geodatabase doesn't exist. Needs to be created. Type Yes")
                continue
        else:
            print ("Staging Geodatabase doesn't exist. Needs to be created. Type Yes")
            continue
    except Exception as e:
        print (e)
        exit()

# print "Begin list of all fields that exists"
Strd_fields = arcpy.ListFields(parcel_out_data)
for field in Strd_fields:
    # print ("{0} type: {1} length: {2}".format(field.name, field.type, field.length))
    log.write("Name: {}".format(field.name) + ", ")
    log.write("Type: {}".format(field.type) + ", ")
    log.write("Length: {}".format(field.length) + "\n")

# Get the list of field names in file and list of predefined field names
# that will be calculated. Missing fields will not crash script, only close.
field_names = [field.name for field in arcpy.ListFields(parcel_out_data)]
match_fields = [i for i in fld_list if i in field_names]
unmatch_fields = [i for i in fld_list if i not in field_names]


Create new GDB and Feature Class? (Yes/No)No
It's a go!


#### Get Year

In [39]:
# Get current year
current_year = datetime.datetime.today().year

#### List of variation of all federal, state and local agencies found in assessor datasets

In [40]:
fedOwnList = ("USA FOREST SERVICE", "USDA FOREST SERVICE", "USDA - FOREST SERVICE", "UNITED STATES POSTAL", 
              "UNITED STATES OF AMERICA", "UNITED STATES FOREST SERVICE", "U S POSTAL SERVICE", "U S COAST GUARD",
              "U S A FOREST SERVICE``", "U S A FOREST SERVICE", "LAKE VALLEY RANGER STA", "DEPT OF VETRANS AFFAIRS%", 
              "DEPT OF VETERANS AFFAIRS%", "DEPT OF VETERANS AFFAIRS %", "BUREAU OF LAND MANAGEMENT", "U S FOREST SERVICE")

stateOwnList = ("TAHOE CONSERVANCY", "STATE OF NEVADA FOREST SERVICE", "STATE OF NEVADA", "STATE OF CALIFORNIA THE", 
                "STATE OF CALIFORNIA (EASEMENT)", "STATE OF CALIFORNIA", "STATE OF CA", "REGENTS OF UNIV OF CALIF", 
                "NEVADA, STATE OF", "NEVADA STATE OF", "CALIFORNIA TAHOE CONSERVANCY ET AL", "CALIFORNIA TAHOE CONSERVANCY"
                "CALIFORNIA STATE OF THE", "CALIFORNIA STATE OF ET AL", "CALIFORNIA STATE OF")

localOwnList = ("ZEPHYR COVE GENERAL IMP DIST", "WASHOE COUNTY SCHOOL DISTRICT BOARD", "WASHOE COUNTY", "WASHOE TRIBE OF NV & CA", 
                "TALMONT RESORT IMPROVEMENT DISTRICT", "TALMONT RESORT IMPR DIST", "TALMONT RESORT IMP DISTRICT",
                "TALMONT RESORT IMP DIST", "TAHOE PARADISE RESORT IMP DIST", "TAHOE PARADISE RES IMP DST",
                "TAHOE FOREST HOSPITAL DISTRICT", "TAHOE TRUCKEE UNIFIED SCHOOL DISTRICT", "TAHOE TRUCKEE UNIFIED SCH DIST", 
                "TAHOE DOUGLAS FIRE PROTECT DIST", "TAHOE DOUGLAS SEWER DIST", "TAHOE DOUGLAS DISTRICT", 
                "TAHOE CITY PUBLIC UTILITY DISTRICT", "TAHOE CITY PUBLIC UTILITY DIST", "TAHOE CITY PUBLIC UTILDIST", 
                "TAHOE CITY PUB UTILITY DST", "TAHOE CITY PUB UTILITY DIS", "TAHOE CITY P U D", "TAHOE CITY CEMETERY DIST", 
                "SOUTH TAHOE REDEVELP AGENCY", "SOUTH TAHOE REFUSE CO", "SOUTH TAHOE PUD", "SOUTH TAHOE PUBLIC UTL DST",
                "SOUTH TAHOE PUBLIC UTILITYDIST", "SOUTH TAHOE PUBLIC UTILITY DST", "SOUTH TAHOE PUBLIC UTILITY DIS", 
                "SOUTH TAHOE PUBLIC UTILITY", "SOUTH TAHOE PUBLIC UTIL DT", "SOUTH TAHOE PUBLIC UTIL DIST", 
                "SOUTH TAHOE PUBLIC", "SOUTH TAHOE PUB UTIL DIST", "SOUTH LAKE TAHOE CTYOF 1/3", "SOUTH LAKE TAHOE CITY OF", 
                "SO TAHOE PUBLIC UTILITY DIST", "SO TAHOE PUB UTIL DIST", "SIERRA NEVADA COLLEGE", "ROUND HILL GEN IMP DIST",
                "PLACER COUNTY REDEVELOPMENT AGENCY", "PLACER COUNTY OF", "PLACER COUNTY", "NORTH TAHOE PUBLIC UTL DIST",
                "NORTH TAHOE PUBLIC UTILITY DISTRICT", "NORTH TAHOE PUBLIC UTILITY DIST", "NORTH TAHOE PUBLIC UTILITY DIS", 
                "NORTH TAHOE PUBLIC UTILITIES DIST", "NORTH TAHOE PUBLIC UTILIITY DISTRICT", "NORTH TAHOE P U D",
                "NORTH TAHOE FIRE PROTECTION DISTRICT", "NORTH TAHOE FIRE PROTECTION", "NORTH TAHOE FIRE DIST",
                "NORTH LAKE TAHOE FIRE PROTECTION DIST", "N TAHOE FIRE PROTECTION DIST", "MEEKS BAY FIRE PROT DIST", 
                "LAKERIDGE GENERAL IMP DIST", "LAKE VALLEY FIRE PROTECTION", "LAKE VALLEY FIRE PROT DST", "LAKE VALLEY FIRE PROT DIST", 
                "LAKE VALLEY FIRE DISTRICT", "LAKE TAHOE UNIFIED SCHOOL DIST", "LAKE TAHOE SCHOOL", "LAKERIDGE GENERAL IMP DIST", 
                "LAKE TAHOE FIRE PROTECTION DIST", "LAKE TAHOE FIRE PROTECT DIST", "LAKE TAHOE COMM COLLEGE DIST",
                "LAKE TAHOE COMM COL DIST", "KINGSBURY GENERAL IMP DISTRICT", "KINGSBURY GENERAL IMP DIST",
                "INCLINE VILLAGE GENERAL IMPROVEMENT DISTRICT", "INCLINE VILLAGE GENERAL IMPROVEMENT DIST", 
                "DOUGLAS COUNTY SEWER DIST", "DOUGLAS COUNTY SCHOOL DIST", "DOUGLAS COUNTY", "DOUGLAS CO SEWER IMP DIST #1", 
                "COUNTY OF EL DORADO", "CITY OF SOUTH LAKE TAHOE", "EL DORADO IRRIGATION DISTRICT", 
                "HAPPY HOMESTEAD CEMETERY DIST") 

ownerListVal = ("STATE OF NEVADA", "STATE OF NEVADA FOREST SERVICE", "NEVADA, STATE OF",
                "NEVADA, DEPT OF TRANSPORTATION",
                "STATE OF CALIFORNIA (EASEMENT)", "STATE OF CALIFORNIA", "CALIFORNIA STATE OF", "STATE OF CALIFORINA",
                "STATE OF CALIFORIA", "STATE OF CA", "CALIFORNIA STATE OF ET AL",
                "UNITED STATES OF AMERICA", "U S A FOREST SERVICE", "U S A  FOREST SERVICE", "USA FOREST SERVICE",
                "U S COAST GUARD", "BUREAU OF LAND MANAGEMENT", "DEPT OF VETRANS AFFAIRS", "DEPT OF VETERANS AFFAIRS",
                "DEPT OF VETERANS AFFAIRS %",
                "U S FOREST SERVICE", "UNITED STATES FOREST SERVICE", "UNITED STATES POSTAL",
                "CARSON CITY", "DOUGLAS COUNTY",
                "CITY OF SOUTH LAKE TAHOE", "COUNTY OF EL DORADO", "EL DORADO COUNTY OF", "PLACER COUNTY",
                "PLACER COUNTY OF", "PLACER COUNTY REDEVELOPMENT AGENCY",
                "DOUGLAS COUNTY SCHOOL DIST", "DOUGLAS CO SEWER IMP DIST #1", "LAKE TAHOE UNIFIED SCHOOL DIST",
                "TALMONT RESORT IMP DIST", "TALMONT RESORT IMP DISTRICT",
                "TALMONT RESORT IMPROVEMENT DISTRICT", "CALIFORNIA TAHOE CONSERVANCY", "CA TAHOE CONSERVANCY",
                "LAKE TAHOE COMM COL DIST",
                "SO TAHOE PUB UTIL DIST", "SO TAHOE PUBLIC UTILITY DIST", "SOUTH TAHOE PUB UTIL DIST",
                "SOUTH TAHOE PUBLIC UTIL DIST", "SOUTH TAHOE PUBLIC UTIL DT",
                "SOUTH TAHOE PUBLIC UTILITY DIS", "SOUTH TAHOE PUBLIC UTILITY DST", "SOUTH TAHOE PUBLIC UTL DST",
                "SOUTHTAHOE PUBLIC UTILITY DIST", "CALIFORNIA TAHOE CONSERVANCY ET AL")


#### List all field names and their index number

In [16]:
field_names = [field.name for field in arcpy.ListFields(parcel_out_data)]
# lists the index of the field names in parcel out data
for index, field in enumerate(field_names):
    print (index, field)

0 OBJECTID_1
1 Shape
2 OBJECTID
3 POLY_ID
4 PRCL_ID
5 EXCPTN_ID
6 POLY_CLASS
7 POLY_CREAT
8 POLY_DESCR
9 APN_STATUS
10 USECDPRI
11 USECDPRICL
12 USECDPRITY
13 USECDPRILI
14 USECDSEC
15 USECDSECCL
16 USECDSECTY
17 USECDSECLI
18 ACREAGE
19 LEGAL_DESC
20 SUBDIV
21 SUBDIV_LIT
22 SITUSNUMBR
23 SITUSSTRNM
24 SITUSSTRTY
25 UNIT_TYPE
26 UNIT_NBR
27 STRUCVAL
28 LANDVAL
29 OWNER_NAME
30 OWNER_ADDR
31 OWNER_CITY
32 OWNER_STAT
33 OWNER_ZIP
34 OWNER_ZIPS
35 OWNER_CNTR
36 CITY
37 SUPR_LIT
38 TRA_PRI
39 TRA_SEC
40 SCHL_LIT
41 FIRE_LIT
42 WATR_LIT
43 AREA
44 PERIMETER
45 PRCL_IDMB
46 Shape_Length
47 Shape_Area
48 APN_NEW
49 PPNO_NEW
50 HSE_NUMBR_NEW
51 UNIT_NUMBR_NEW
52 STR_DIR_NEW
53 STR_NAME_NEW
54 STR_SUFFIX_NEW
55 APO_ADDRESS_NEW
56 PSTL_TOWN_NEW
57 PSTL_STATE_NEW
58 PSTL_ZIP5_NEW
59 OWN_FIRST_NEW
60 OWN_LAST_NEW
61 OWN_FULL_NEW
62 MAIL_ADD1_NEW
63 MAIL_ADD2_NEW
64 MAIL_CITY_NEW
65 MAIL_STATE_NEW
66 MAIL_ZIP5_NEW
67 JURISDICTION_NEW
68 COUNTY
69 OWNERSHIP_TYPE
70 UNITS_NEW
71 COUNTY_LANDUSE
72 COU

### Translate County Values to TRPA Values and Fields

In [16]:
# process Washoe County fields
if UserCountyResponse == "Washoe":
    print ("Processing the {} dataset".format(County_List[4]))
    with arcpy.da.UpdateCursor(parcel_out_data, field_names) as cursor:
    field_names = ['APN', 'APN_NEW', 'PIN', 'PPNO_NEW',
                   'STREETNUM','HSE_NUMBR_NEW','UNIT_NUMBR_NEW', 'STREETDIR', 'STR_DIR_NEW',
                   'STREET', 'STR_NAME_NEW', 'STR_SUFFIX_NEW','PSTL_STATE_NEW',
                   'FIRSTNAME', 'OWN_FIRST_NEW', 'LASTNAME', 'OWN_LAST_NEW', 'OWN_FULL_NEW',
                   'MAILING1','MAIL_ADD1_NEW', 'MAILING2','MAIL_ADD2_NEW',
                   'MAILCITY', 'MAIL_CITY_NEW', 'MAILSTATE','MAIL_STATE_NEW', 
                   'MAILZIP',  'MAIL_ZIP5_NEW', 'JURISDICTION_NEW','COUNTY', 'OWNERSHIP_TYPE',
                   'LAND_USE', 'COUNTY_LANDUSE', 
                   'LANDASS', 'AS_LANDVALUE_NEW','BUILDASS','AS_IMPROVALUE_NEW','AS_SUM_NEW',
                   'LANDAPR','TAX_LANDVALUE_NEW','BUILDAPR','TAX_IMPROVALUE_NEW','BUILDAPR','TAX_SUM_NEW','TAX_YEAR_NEW']
        for row in cursor:
            # set apn
            apn = row[0]
            if not (apn is None or apn == "" or apn.isspace() == True):
                row[1] = apn
            else:
                row[1] = ""
            # set ppno
            ppno = row[2
            if not ppno is None:
                row[3] = int(ppno)
            else:
                row[3] = ""
            # set house number
            hsenumbr = row[4]
            if not (hsenumbr is None or hsenumbr == "" or hsenumbr.isspace() == True):
                row[5] = (hsenumbr.strip())
            else:
                row[5] = 0
            # set unit number (doesn't exist in WA data)
            row[6] = ""
            # set street direction
            stdir = row[7]
            if not stdir is None:
                row[8] = (stdir.strip())
            else:
                row[8] = ""
            # set street name    
            stname = row[9]
            if not (stname is None or stname in ('CROSS BOW', 'ENTERPRISE','STATE ROUTE 28', 'UNSPECIFIED', 'US HIGHWAY 395 S', '')):
                row[10] = (stname.rsplit(" ", 1)[0].strip())
            elif stname in ('CROSS BOW', 'ENTERPRISE', 'STATE ROUTE 28', 'UNSPECIFIED', 'US HIGHWAY 395 S', ''):
                row[10] = (stname.strip())
            else:
                row[10] = ""
            # set street suffix
            stname = row[9]
            if not stname in ('CROSS BOW', 'ENTERPRISE', 'STATE ROUTE 28', 'UNSPECIFIED', 'US HIGHWAY 395 S', ''):
                row[11] = (stname.rsplit(" ", 1)[1].strip())
            else:
                row[11] = ""
            # set postal town with spatial join
            # set postal state
            row[12] = "NV"
            # set postal zip with spatial join
            # set owner first name
            ownfirst = row[13]
            if not (ownfirst is None or ownfirst.isspace() == True):
                row[14] = ownfirst
            else:
                row[14] = ""
            # set owner last name
            ownlast = row[15]
            if not (ownlast is None or ownlast.isspace() == True):
                row[16] = ownlast
            else:
                row[16] = ""
            #set owner full name
            if not (ownfirst is None and ownlast is None):
                row[17] = (ownfirst + " " + ownlast).strip()
            else:
                row[17] = ""
            # set mail1
            mail1 = row[18]
            if not (mail1 is None or mail1 == "" or mail1.isspace() == True or mail1 == "NONE" or mail1 == "NOT SUPPLIED"):
                row[19] = mail1
            else:
                row[19] = ""
            # set mial address 2
            mail2 = row[20]
            if not (mail2 is None or mail2 == "" or mail2.isspace() == True) and ("ATTN" in mail2 or "C/O" in mail2 or "P O BOX" in mail2 or "PMB" in mail2):
                row[21] = mail2
            else:
                row[21] = ""
            # set mail city
            mailcity = row[22]
            if not (mailcity is None or mailcity == "" or mailcity == "NONE" or mailcity.isspace() == True):
                row[23] = mailcity
            else:
                row[23] = ""
            # set mail state
            mailstate = row[24]
            if not (mailstate is None or mailstate == "" or mailstate.isspace() == True):
                row[25] = mailstate
            else:
                row[25] = ""
            # set mail zip
            mailzip = row[26]
            if not (mailzip is None or mailzip == "" or mailzip.isspace() == True):
                row[27] = mailzip[:5]
            else:
                row[27] = ""
            # set jurisdiction
            row[28] = County_ABR
            # set county
            row[28] = County_ABR
            # set ownership type
            if not (ownlast is None or ownlast == "" or ownlast.isspace() == True):
                if ownlast in fedOwnList:
                    row[29] = "Federal"
                elif ownlast in localOwnList:
                    row[29] = "Local"
                elif ownlast in stateOwnList:
                    row[29] = "State"
                elif not ownlast in (fedOwnList, localOwnList, stateOwnList):
                    row[29] = "Private"
            # set county land use code
            ctyluc = row[30]
            if not (ctyluc is None or ctyluc == "" or ctyluc.isspace() == True):
                row[31] = int(ctyluc)
            else:
                row[31] = ""
            # set assessed land value
            landval = row[32]
            row[33] = landval
            # set assessed improved value
            improval = row[34]
            row[35] = improval
            # set assessed sum
            if not (landval is None or improval is None):
                row[36] = landval + improval
            else:
                row[36] = ""
            # set tax land value
            if not landval is None:
                row[37] = (landval/0.35)
            else:
                row[37] = ""
            # set tax improved value
            if not improval is None:
                row[38] = (improval/0.35)
            else:
                row[38] = ""
            # set tax sum
            if not (landval is None or improval is None):
                row[39] = (landval + improval)
            else:
                row[39] = ""
            # set tax year
            row[40] = current_year
            # update all rows
            cursor.updateRow(row)
        print ("Rows in {} county staging dataset have been updated".format(County_List[4]))       
# ----------------------------------------------------------------------------------------------
elif UserCountyResponse == "Carson":
    print ("Processing the {} dataset".format(County_List[0]))
    
    with arcpy.da.UpdateCursor(parcel_out_data, field_names) as cursor:
    field_names = ['APN', 'APN_NEW', 'PPNO', 'PPNO_NEW','PLOC_','HSE_NUMBR_NEW','PLOCU_','UNIT_NUMBR_NEW', 'PLOCDR', 'STR_DIR_NEW',
                   'PLOCNM', 'STR_NAME_NEW', 'PLOCTP', 'STR_SUFFIX_NEW', 'PSTL_TOWN_NEW', 'PSTL_STATE_NEW','PSTL_ZIP5_NEW',
                   'PANAME', 'OWN_FIRST_NEW', 'OWN_LAST_NEW', 'OWN_FULL_NEW','PMADD1','MAIL_ADD1_NEW', 'PMADD2',
                   'MAIL_ADD2_NEW', 'PMCTST', 'MAIL_CITY_NEW', 'MAIL_STATE_NEW', 'PZIP',  'MAIL_ZIP5_NEW', 'JURISDICTION_NEW',
                   'COUNTY', 'OWNERSHIP_TYPE', 'UNITS_NEW', 'YLDUSE', 'COUNTY_LANDUSE', 'YLANDV', 'AS_LANDVALUE_NEW',
                   'YIMPRV','AS_IMPROVALUE_NEW','AS_SUM_NEW','TAX_LANDVALUE_NEW','TAX_IMPROVALUE_NEW','TAX_SUM_NEW',
                   'TAX_YEAR_NEW']
        for row in cursor:
            # set APN
            apn = row[0]
            row[1] = (apn[:3] + sep + apn[3:6] + sep + apn[6:8])
            # set PPNO
            row[2] = (apn)
            # set house number
            hsenum = row[3]
            if hsenum > 0:
                row[4] = hsenum
            else:
                row[4] = 0
            # set unit number
            row[5] = ""
            # set street direction
            stdir = row[34]
            if not stdir is None:
                row[63] = stdir
            else:
                row[63] = ""
            # set street name 
            stname = row[35]
            if not stname is None:
                row[64] = stname
            else:
                row[64] = ""
            # set street suffix
            row[65] = ""
            # APO Address set at the end
            # set postal town
            row[67] = 'Carson City'
            # set postal state
            row[68] = 'NV'
            # set postal zip
            row[69] = '89703' 
            # set owner first name
            own = row[27]
            if not (own is None or own == "" or own.isspace() == True):
                    try:
                        if own not in ownerListVal:
                            row[70] = (own.split(" ")[0].strip())
                    except IndexError:
                        row[70] = ""
            else:
                row[70] = ""
            # set owner last name
            if not (own is None or own == "" or own.isspace() == True):
                    try:
                        if own in ownerListVal:
                            row[71] = own
                        else:
                            row[71] = own.split(" ", 1)[1].strip()
                    except IndexError:
                        row[71] = ""
            else:
                row[71] = ""
            # set owner full name
            if not (own is None or own == "" or own.isspace() == True):
                row[72] = own
            else:
                row[72] = ""
            # set mail address 1
            mail1 = row[29]
            if not (mail1 is None or mail1 == "" or mail1.isspace() == True):
                row[73] = mail1.replace("%", "").strip()
            else:
                row[73] = ""
            # set mail address 2
            mail2 = row[30]
            if not (mail2 is None or mail2 == "" or mail2.isspace() == True) and (
            "ATTN" in mail2 or "C/O" in mail2 or "P O BOX" in mail2 or "PMB" in mail2):
                row[74] = mail2
            else:
                row[74] = ""
            # set mail city
            mailcity = row[31]
            if not (mailcity is None or mailcity == "" or mailcity.isspace() == True):
                row[75] = mailcity.split(",")[0].strip()
            else:
                row[75] = ""
            # set mail state
            mailstate = row[31]
            if "," in mailstate:
                mailstate = mailcity.split(",")[1].strip()
                row[76] = mailstate
            else:
                mailstate = ""
                row[76] = mailstate
            # set mail zip
            mailzip = row[32]
            if not (mailzip is None or mailzip == "" or mailzip.isspace() == True):
                row[77] = mailzip[:5]
            else:
                row[77] = ""
            # set jurisdiction
            row[78] = County_ABR
            #set county
            row[79] = County_ABR
            # set ownership type
            if not (own is None or own == "" or own.isspace() == True):
                if own in fedOwnList:
                    row[80] = "Federal"
                elif own in localOwnList:
                    row[80] = "Local"
                elif own in stateOwnList:
                    row[80] = "State"
                elif not own in (fedOwnList, localOwnList, stateOwnList):
                    row[80] = "Private"
            # set units
            row[81] = 0
            # set county land use
            ctyluc = row[20]
            if ctyluc is not None:
                row[82] = ctyluc
            else:
                row[82] = ""
            # set assessed land value
            landval = row[42]
            if not landval is None:
                row[98] = landval
            else:
                row[98] = ""
            # set assessed improved value
            improval = row[43]
            if not improval is None:
                row[99] = improval
            else:
                row[99] = ""
            # set assessed sum
            row[118] = landval + improval
            # set tax land value
            taxland = landval / 0.35
            row[119] = taxland
            # set tax improved value
            taximprov = improval / 0.35
            row[120] = taximprov
            # set tax sum value
            row[121] = taxland + taximprov
            # set tax year
            row[122] = current_year
            
            # update all rows
            cursor.updateRow(row)
        print ("Rows in {} dataset have been updated".format(County_List[0]))
# ----------------------------------------------------------------------------------------------
elif UserCountyResponse == "Douglas":
    print ("Processing the {} dataset".format(County_List[1]))
    field_names = ['APN', 'APN_NEW', 'PPNO', 'PPNO_NEW','PLOC_','HSE_NUMBR_NEW','PLOCU_','UNIT_NUMBR_NEW', 'PLOCDR', 'STR_DIR_NEW',
                   'PLOCNM', 'STR_NAME_NEW', 'PLOCTP', 'STR_SUFFIX_NEW', 'PSTL_TOWN_NEW', 'PSTL_STATE_NEW','PSTL_ZIP5_NEW',
                   'PANAME', 'OWN_FIRST_NEW', 'OWN_LAST_NEW', 'OWN_FULL_NEW','PMADD1','MAIL_ADD1_NEW', 'PMADD2',
                   'MAIL_ADD2_NEW', 'PMCTST', 'MAIL_CITY_NEW', 'MAIL_STATE_NEW', 'PZIP',  'MAIL_ZIP5_NEW', 'JURISDICTION_NEW',
                   'COUNTY', 'OWNERSHIP_TYPE', 'UNITS_NEW', 'YLDUSE', 'COUNTY_LANDUSE', 'YLANDV', 'AS_LANDVALUE_NEW',
                   'YIMPRV','AS_IMPROVALUE_NEW','AS_SUM_NEW','TAX_LANDVALUE_NEW','TAX_IMPROVALUE_NEW','TAX_SUM_NEW',
                   'TAX_YEAR_NEW']
    with arcpy.da.UpdateCursor(parcel_out_data, field_names) as cursor:
        for row in cursor:
            # set apn
            apn = row[0]
            if not (apn is None or apn == ""):
                row[1] = (str(apn)[:4] + sep + str(apn)[4:6] + sep + str(apn)[6:9] + sep + str(apn)[9:12])
            else:
                row[1] = ""
            # set ppno
            ppno = row[2]
            if not ppno is None:
                row[3] = ppno
            else:
                row[3] = 0
            # set house number
            hsenumbr = row[4]
            if hsenumbr > 0:
                row[5] = hsenumbr
            else:
                row[5] = 0
            # set unit number
            unit = row[6]
            if not unit is None:
                row[7] = unit
            else:
                row[7] = ""
            # set street direction
            stdir = row[8]
            if not stdir is None:
                row[9] = stdir
            else:
                row[9] = ""
            # set street name
            stname = row[10]
            if not stname is None:
                row[11] = stname
            else:
                row[11] = ""
            # set street suffix
            stsuf = row[12]
            if not stsuf is None:
                row[13] = stsuf
            else:
                row[13] = ""
            # set postal town
            row[14] = ""
            # set postal state
            row[15] = "NV"
            # set postal zip
            row[16] = ""
            # set owner fist name
            own = row[17]
            if not own is None or own == "" or own.isspace() == True:
                try:
                    if own not in ownerListVal:
                        row[18] = own.split(",", 1)[1].strip()
                    else:
                        row[18] = ""
                except IndexError:
                    row[18] = ""
            else:
                row[18] = ""
            # set owner last name
            if not own is None or own == "" or own.isspace() == True:
                try:
                    if own in ownerListVal:
                        row[19] = own
                    else:
                        row[19] = own.split(",")[0].strip()
                except IndexError:
                    row[19] = ""
            else:
                row[19] = ""
            # set owner fullname
            if not own is None:
                row[20] = own.strip()
            else:
                row[20] = ""
            
            # set mail address 1
            mail1 = row[23]
            if not mail1 is None or mail1 == "" or mail1.isspace() == True:
                row[22] = mail1.strip()
            else:
                row[22] = ""
            # set mail address 2
            mail2 = row[21]
            if not (mail2 is None or mail2 == "" or mail2.isspace() == True) and (
                            "ATTN" in mail2 or "C/O" in mail2 or "PO BOX" in mail2 or "PMB" in mail2):
                row[24] = mail2.strip()
            else:
                row[24] = ""
            # set mail city
            mailcity = row[25]
            if not mailcity is None or mailcity == "" or mailcity.isspace() == True:
                if "," in mailcity:
                    row[26] = mailcity.split(",")[0].strip()
            else:
                row[26] = ""
            # set mail state
            if not mailcity is None or mailcity == "" or mailcity.isspace() == True:
                if "," in mailcity:
                    mailstate = mailcity.split(",")[1].strip()
                    if len(mailstate) > 2:
                        row[27] = ""
                        print ("International Address, {}".format(mailstate))
                    else:
                        row[27] = mailstate
            else:
                row[27] = ""
            # set mail zip code
            mailzip = row[28]
            if not (mailzip is None or mailzip == "" or mailzip.isspace() == True):
                row[29] = mailzip[:5]
            else:
                row[29] = ""
            # set jurisdiction
            row[30] = County_ABR
            # set county
            row[31] = County_ABR
            # set ownership type
            if not (own is None or own == "" or own.isspace() == True):
                if own in fedOwnList:
                    row[32] = "Federal"
                elif own in localOwnList:
                    row[32] = "Local"
                elif own in stateOwnList:
                    row[32] = "State"
                elif not own in (fedOwnList, localOwnList, stateOwnList):
                    row[32] = "Private"
            # set units
            row[33] = 0
            # set county land use code
            ctyluc = row[34]
            row[35] = ctyluc
            # set assessed land value
            landval = row[36]
            if not landval is None:
                row[37] = landval
            else:
                row[37] = ""
            # set assessed improved value
            improval = row[38]
            if not improval is None:
                row[39] = improval
            else:
                row[39] = ""
            # set assessed sum
            row[40] = landval + improval
            # set tax land value
            taxland = landval / 0.35
            row[41] = taxland
            # set tax improved value
            taximprov = improval / 0.35
            row[42] = taximprov
            # set tax sum value
            row[43] = taxland + taximprov
            # set tax year
            row[44] = current_year
            
            cursor.updateRow(row)
        print ("Rows in {} dataset have been updated".format(County_List[1]))
# ----------------------------------------------------------------------------------------------
elif UserCountyResponse == "El_Dorado":
    print("Processing the {} dataset".format(County_List[2]))
    field_names = ['PRCL_ID', 'APN_NEW','PPNO_NEW','SITUSNUMBR','HSE_NUMBR_NEW','UNIT_NBR','UNIT_NUMBR_NEW', 
                   'STR_DIR_NEW','SITUSSTRNM', 'STR_NAME_NEW', 'SITUSSTRTY', 'STR_SUFFIX_NEW', 'PSTL_STATE_NEW',
                   'OWNER_NAME', 'OWN_FIRST_NEW', 'OWN_LAST_NEW', 'OWN_FULL_NEW',
                   'OWNER_ADDR','MAIL_ADD1_NEW','MAIL_ADD2_NEW', 'OWNER_CITY', 'MAIL_CITY_NEW', 'OWNER_STAT','MAIL_STATE_NEW', 
                   'OWNER_ZIP',  'MAIL_ZIP5_NEW', 'JURISDICTION_NEW','COUNTY', 'OWNERSHIP_TYPE',
                   'USECDPRI', 'COUNTY_LANDUSE', 'USECDPRILI',
                   'LANDVAL', 'AS_LANDVALUE_NEW','STRUCVAL','AS_IMPROVALUE_NEW','AS_SUM_NEW',
                   'TAX_LANDVALUE_NEW','TAX_IMPROVALUE_NEW','TAX_SUM_NEW','TAX_YEAR_NEW']
    with arcpy.da.UpdateCursor(parcel_out_data, field_names) as cursor:
        for row in cursor:
            # set apn
            apn = row[0]
            if not (apn is None or apn == "" or apn.isspace() == True or 'UN' in apn):
                row[1] = (apn[:3] + sep + apn[3:6] + sep + apn[6:8])
            else:
                row[1] = ""
            # set ppno
            ppno = row[0]
            if not (apn is None or apn == "" or apn.isspace() == True or 'UN' in apn):
                try:
                    row[2] =  ppno
                except ValueError:
                    row[2] = ""
            else:
                row[2] = ""
             # set house number
            hsenum = row[3]
            row[4] = hsenum
            # set unit number
            unit = row[5]
            if not unit is None:
                row[6] = "#" + unit
            else:
                row[6] = ""
            # set street direction doesnt exist in El Dorado data
            row[7] = ""
            # set street name
            stname = row[8]
            if not stname is None:
                row[9] = stname
            else:
                row[9] = ""
            # set street suffix
            stsuff = row[10]
            if not stsuff is None:
                row[11] = stsuff
            else:
                row[11] = ""
            # set postal town and postal zip with spatial join....later in the python notebook....scroll down
            # set postal state
            row[12] = "CA"
            # set owner full name
            own = row[13]
            row[16] = own
            # set owner first name
            if not own is None or own == "" or own.isspace() == True:
                try:
                    if own not in ownerListVal:
                        row[14] = own.split(" ", 1)[1].strip()
                except IndexError:
                    row[14] = ""
            else:
                row[14] = ""
            # set owner last name
            if not own is None or own == "" or own.isspace() == True:
                try:
                    if own in ownerListVal:
                        row[15] = own
                    else:
                        row[15] = own.split(" ")[0].strip()
                except IndexError:
                    row[15] = ""
            else:
                row[15] = ""
            # set mail1
            mail1 = row[17]
            if not mail1 is None or mail1 == "" or mail1.isspace() == True:
                row[18] = mail1.replace("%", "").strip()
            else:
                row[18] = ""
            # set mail2
            row[19] = ""
            # set mail city
            mailcity = row[20]
            if not mailcity is None or mailcity == "" or mailcity.isspace() == True:
                row[21] = mailcity
            else:
                row[21] = ""
            # set mail state
            mailstate = row[22]
            if not mailstate is None or mailstate == "" or mailstate.isspace() == True:
                row[23] = mailstate
            else:
                row[23] = ""
            # set mail zip
            mailzip = row[24]
            if not mailzip is None or mailzip == "" or mailzip.isspace() == True:
                row[25] = mailzip[:5]
            else:
                row[25] = ""
            # set jurisdiction
            row[26] = County_ABR
            # set county
            row[27] = County_ABR
            # set ownership type
            if not (own is None or own == "" or own.isspace() == True):
                if own in fedOwnList:
                    row[28] = "Federal"
                elif own in localOwnList:
                    row[28] = "Local"
                elif own in stateOwnList:
                    row[28] = "State"
                elif not own in (fedOwnList, localOwnList, stateOwnList):
                    row[28] = "Private"
            # set county land use code
            ctyluc = row[29]
            if not ctyluc is None or ctyluc == "" or ctyluc.isspace() == True:
                row[30] = ctyluc
            else:
                row[30] = ""
            # set assessed land value
            landval = row[31]
            row[32] = landval
            # set assessed improved value
            improval = row[33]
            row[34] = improval
            # set assessed sum
            row[35] = improval + landval
            # set tax land value
            taxland = row[31]
            row[36] = taxland
            # set tax improved value
            taximprov = row[33]
            row[37] = taximprov
            # set tax sum
            row[38] = taxland + taximprov
            # set tax year
            row[39] = current_year

            # set postl zip with spatial join
            # set number of units
            
            cursor.updateRow(row)
        print ("Rows in {} dataset have been updated".format(County_List[2]))
# ----------------------------------------------------------------------------------------------
elif UserCountyResponse == "Placer":
    print ("Processing the {} dataset".format(County_List[3]))
    field_names = ['APN', 'APN_NEW','GISAPN', 'PPNO_NEW','STREETNUM','HSE_NUMBR_NEW','SP_APT','UNIT_NUMBR_NEW', 
                   'STREETDIR', 'STR_DIR_NEW','STREETNAME', 'STR_NAME_NEW', 'STREETTYPE', 'STR_SUFFIX_NEW', 'PSTL_STATE_NEW',
                   'OWNER1', 'OWN_FIRST_NEW', 'OWNER2', 'OWN_LAST_NEW', 'OWN_FULL_NEW',
                   'ADR1','MAIL_ADD1_NEW', 'MAIL_ADD2_NEW','CITY', 'MAIL_CITY_NEW', 'STATE','MAIL_STATE_NEW', 
                   'ZIP',  'MAIL_ZIP5_NEW', 'JURISDICTION_NEW','COUNTY', 'OWNERSHIP_TYPE',
                   'USE_CD', 'COUNTY_LANDUSE', 'USE_CD_N', 'COUNTY_LANDUSE_DESCRIPTION',
                   'LANDVALUE', 'AS_LANDVALUE_NEW','STRUCTURE','AS_IMPROVALUE_NEW','AS_SUM_NEW',
                   'TAX_LANDVALUE_NEW','TAX_IMPROVALUE_NEW','TAX_SUM_NEW','TAX_YEAR_NEW']
    with arcpy.da.UpdateCursor(parcel_out_data, field_names) as cursor:
        for row in cursor:
            # set apn
            apn = row[0]
            if not (apn is None or apn == "" or apn.isspace() == True or "ROW" in apn or len(apn) < 8):
                row[1] = apn[:11]
            else:
                row[1] = ""
            # set ppno
            ppno = row[2]
            if not (ppno is None or ppno == "" or ppno.isspace() == True or "ROW" in ppno or len(ppno) < 8):
                row[3] =  int(ppno)
            else:
                row[3] = 0
            # set house number
            hsenumbr = row[4]
            if not (hsenumbr is None or hsenumbr == "" or hsenumbr.isspace() == True):
                try:
                    if hsenumbr.isdigit():
                        row[5] = hsenumbr
                    elif "'" in hsenumbr:
                        row[5] = hsenumbr.replace("'", "").strip()
                    else:
                        pass
                except RuntimeError:
                    row[5] = 0
            else:
                row[5] = 0
            # set unit number
            unit = row[6]
            if not unit is None:
                row[7] = "#" + unit
            else:
                row[7] = ""
            # set street direction
            stdir = row[8]
            if not stdir is None:
                row[9] = stdir
            else:
                row[9] = ""
            # set street name
            stname = row[10]
            if not stname is None:
                row[11] = stname
            else:
                row[11] = ""
            # set street suffix
            stsuff = row[12]
            if not stsuff is None:
                row[13] = stsuff
            else:
                row[13] = ""
            # set postal state
            row[14] =  "CA"
            
            # set postal town and postal zip with spatial join....scroll down
            # set owner full name
            own = row[15]
            row[18] = own
            # set owner first name
            if not (own is None or own == "" or own.isspace() == True):
                try:
                    if own not in ownerListVal:
                        row[16] = own.split(" ", 1)[1].strip()
                except IndexError:
                    row[16] = ""
            else:
                row[16] = ""
            # set owner last name
            if not (own is None or own == "" or own.isspace() == True):
                try:
                    if own in ownerListVal:
                        row[17] = own
                    else:
                        row[17] = own.split(" ")[0].strip()
                except IndexError:
                    row[17] = ""
            else:
                row[17] = ""
            # set mail1
            mail1 = row[19]
            if not (mail1 is None or mail1 == "" or mail1.isspace() == True):
                row[20] = mail1
            else:
                row[20] = ""
            # set mail2
            mail2 = row[21]
            if not (mail2 is None or mail2 == "" or mail2.isspace() == True) \
                    and ("ATTN" in mail2 or "C/O" in mail2 or "P O BOX" in mail2 or "PMB" in mail2):
                row[22] = mail2
            else:
                row[22] = ""
            # set mail city
            mailcity = row[23]
            if not (mailcity is None or mailcity == "" or mailcity.isspace() == True or "N/A" in mailcity or \
                    "N\A" in mailcity or "P O BOX" in mailcity or "VALUE" in mailcity or "PRORATED" in mailcity):
                row[24] = mailcity
            else:
                row[24] = ""
            # set mail state
            mailstate = row[25]
            if not (mailstate is None or mailstate == "" or mailstate.isspace() == True or len(mailstate) < 2):
                row[26] = mailstate
            else:
                row[26] = ""
            # set mail zip
            mailzip = row[27]
            if not (mailzip is None or mailzip == "" or mailzip.isspace() == True):
                row[28] = mailzip[:5]
            else:
                row[28] = ""
            # set jurisdiction
            row[29] = County_ABR
            # set county
            row[29] = County_ABR
            # set ownership type
            if not (own is None or own == "" or own.isspace() == True):
                if own in fedOwnList:
                    row[30] = "Federal"
                elif own in localOwnList:
                    row[30] = "Local"
                elif own in stateOwnList:
                    row[30] = "State"
                elif not own in (fedOwnList, localOwnList, stateOwnList):
                    row[30] = "Private"
            # set county land use code
            ctyluc = row[31]
            if not (ctyluc is None or ctyluc == "" or ctyluc.isspace() == True):
                row[32] = ctyluc
            else:
                row[32] = ""

            # set assessed land value
            landval = row[35]
            row[83] = landval
            # set assessed improved value
            improval = row[36]
            row[84] = improval
            # set assessed sum
            if not (landval is None and improval is None):
                row[85] =  landval + improval
            else:
                row[85] = ""
            # set tax land value
            if not (landval is None):
                row[85] =  landval + improval
            else:
                row[86] = ""
            # set tax impoved value
            if not (improval is None):
                row[87] =  improval
            else:
                row[87] = ""
            # set tax sum
            if not (landval is None and improval is None):
                row[88] =  landval + improval
            else:
                row[88] = ""
            # set tax year
            row[89] = current_year
            
            cursor.updateRow(row)
        print ("Rows in {} dataset have been updated".format(County_List[3]))
#----------------------------------------------------------------------------------------            
# Calculate APO_ADDRESS, PARCEL_ACRES, and PARCEL_SQFT
expression = "concat(!HSE_NUMBR_NEW!, !STR_DIR_NEW!, !STR_NAME_NEW!, !STR_SUFFIX_NEW!, !UNIT_NUMBR_NEW!)"
apo_codeblock = """
def concat(*args):
    retval = ""
    sep = " "
    for t in args:
        s = str(t).strip()
        if s != None:
            retval += sep + s
    return retval.lstrip(sep)"""
arcpy.CalculateField_management(parcel_out_data, "APO_ADDRESS_NEW", expression, python_version, apo_codeblock)
print ("Calculated APO_ADDRESS")
arcpy.CalculateField_management(parcel_out_data, "PARCEL_ACRES_NEW", "!shape.area@acres!", python_version, "")
print ("Calculated Parcel Acreage")
arcpy.CalculateField_management(parcel_out_data, "PARCEL_SQFT_NEW", "!shape.area@squarefeet!", python_version, "")
print ("Calculated Parcel SQFT")    
arcpy.CalculateField_management(parcel_out_data, "APO_ADDRESS_NEW", "' '.join(!APO_ADDRESS_NEW!.strip().split())", python_version,"#")
print ("Removed Double Spaces from APO_ADDRESS")

Processing the Douglas dataset
International Address, NEVIS ISLAND
International Address, CA 94612
International Address, TAIWAN
International Address, CANADA  L7T3P3
International Address, CANADA  L7T3P3
International Address, CANADA  L7T3P3
International Address, CANADA  L7T3P3
International Address, UK OX11OEY
International Address, HONG KONG
Rows in Douglas dataset have been updated
Calculated APO_ADDRESS
Calculated Parcel Acreage
Calculated Parcel SQFT
Removed Double Spaces from APO_ADDRESS


### Merge Staging Datasets and Eliminate County Fields

In [23]:
# Parcel staging feature classes to be merged
staging = "F:\\GIS\\ParcelUpdate\\2018_10"
WA_Staging = staging + "\\Washoe\\Modified\\WA_Staging.gdb\\Parcels\\Washoe_Parcels"
#CC_Staging = staging + "\\Carson\\Modified\\CC_Staging.gdb\\Parcels\\Carson_Parcels"
DG_Staging = staging + "\\Douglas\\Modified\\DG_Staging.gdb\\Parcels\\Douglas_Parcels"
EL_Staging = staging + "\\El_Dorado\Modified\EL_Staging.gdb\Parcels\\El_Dorado_Parcels"
PL_Staging = staging + "\\Placer\\Modified\\PL_Staging.gdb\\Parcels\\Placer_Parcels"

# set output staging feature class
Parcel_Master_New = r"F:\GIS\ParcelUpdate\2018_10\Workspace\ParcelUpdate_Workspace.gdb\Parcel_Master_New"

# Create FieldMappings object to manage merge output fields
fieldMappings = arcpy.FieldMappings()

# Add all fields
fieldMappings.addTable(WA_Staging)
#fieldMappings.addTable(CC_Staging)
fieldMappings.addTable(DG_Staging)
fieldMappings.addTable(EL_Staging)
fieldMappings.addTable(PL_Staging)

# Remove all output fields from the field mappings, except fields in field_master list
for field in fieldMappings.fields:
    if field.name not in ['APN_NEW', 'PPNO_NEW', 'HSE_NUMBR_NEW', 'UNIT_NUMBR_NEW', 'STR_DIR_NEW', 'STR_NAME_NEW', 
                'STR_SUFFIX_NEW', 'APO_ADDRESS_NEW', 'PSTL_TOWN_NEW', 'PSTL_STATE_NEW', 'PSTL_ZIP5_NEW', 
                'OWN_FIRST_NEW', 'OWN_LAST_NEW', 'OWN_FULL_NEW', 'MAIL_ADD1_NEW', 'MAIL_ADD2_NEW', 
                'MAIL_CITY_NEW', 'MAIL_STATE_NEW', 'MAIL_ZIP5_NEW', 'JURISDICTION_NEW', 'COUNTY', 'OWNERSHIP_TYPE', 
                'UNITS_NEW', 'COUNTY_LANDUSE', 'COUNTY_LANDUSE_DESCRIPTION', 'TRPA_LANDUSE_DESCRIPTION', 
                'REGIONAL_LANDUSE', 'SOIL_1974', 'SOIL_2003', 'ALLOWABLE_COVERAGE_BAILEY_SQFT', 
                'IMPERVIOUS_SURFACE_SQFT', 'HRA_NAME', 'WATERSHED_NUMBER', 'WATERSHED_NAME', 'PRIORITY_WATERSHED',  
                'BMP_STATUS', 'FIREPD', 'WITHIN_TRPA_BNDY', 'LITTORAL', 'AS_LANDVALUE_NEW', 'AS_IMPROVALUE_NEW', 
                'AS_SUM_NEW', 'TAX_LANDVALUE_NEW', 'TAX_IMPROVALUE_NEW', 'TAX_SUM_NEW', 'TAX_YEAR_NEW', 'PAS_ID', 
                'PAS_NAME', 'INDEX_1987', 'INDEX_1987_HYPERLINK', 'LOCAL_PLAN_HYPERLINK', 'ZONING_NEW', 
                'ZONING_DESCRIPTION', 'SINGLE_FAMILY_DENSITY', 'MULTI_FAMILY_DENSITY', 
                'TOURIST_ACCOMMODATION_DENSITY', 'BED_BREAKFAST_DENSITY', 'TIME_SHARE_DENSITY', 
                'COMMERCIAL_FLOOR_AREA_ALLOWED', 'SECONDARY_DWELLING_UNIT_ALLOWED', 'OVERLAY', 
                'MAX_CP_RES_DENSITY', 'MAX_CP_TAU_DENSITY', 'SPECIAL_PLAN_AREA_OVERLAY', 'TOWN_CENTER', 
                'SPECIAL_AREA', 'SPECIAL_PLANNING_DISTRICT', 'SPECIAL_PLANNING_DISTRICT_TYPE', 
                'LOCATION_TO_TOWNCENTER', 'RETIRED', 'PARCEL_ACRES_NEW', 'PARCEL_SQFT_NEW', 'DUPLICATE']:
        fieldMappings.removeFieldMap(fieldMappings.findFieldMapIndex(field.name))
for field in fieldMappings.fields:
    print ("Created Field Map:", field.name)

# Use Merge tool to move features into single dataset
arcpy.Merge_management([WA_Staging, DG_Staging, EL_Staging, PL_Staging], Parcel_Master_New, fieldMappings)
print ("Created a new parcel dataset")

Created Field Map: APN_NEW
Created Field Map: PPNO_NEW
Created Field Map: HSE_NUMBR_NEW
Created Field Map: UNIT_NUMBR_NEW
Created Field Map: STR_DIR_NEW
Created Field Map: STR_NAME_NEW
Created Field Map: STR_SUFFIX_NEW
Created Field Map: APO_ADDRESS_NEW
Created Field Map: PSTL_TOWN_NEW
Created Field Map: PSTL_STATE_NEW
Created Field Map: PSTL_ZIP5_NEW
Created Field Map: OWN_FIRST_NEW
Created Field Map: OWN_LAST_NEW
Created Field Map: OWN_FULL_NEW
Created Field Map: MAIL_ADD1_NEW
Created Field Map: MAIL_ADD2_NEW
Created Field Map: MAIL_CITY_NEW
Created Field Map: MAIL_STATE_NEW
Created Field Map: MAIL_ZIP5_NEW
Created Field Map: JURISDICTION_NEW
Created Field Map: COUNTY
Created Field Map: OWNERSHIP_TYPE
Created Field Map: UNITS_NEW
Created Field Map: COUNTY_LANDUSE
Created Field Map: COUNTY_LANDUSE_DESCRIPTION
Created Field Map: TRPA_LANDUSE_DESCRIPTION
Created Field Map: REGIONAL_LANDUSE
Created Field Map: SOIL_1974
Created Field Map: SOIL_2003
Created Field Map: ALLOWABLE_COVERAGE_BA

### Change Field Names (eliminate the '_NEW')

In [6]:
import os
import arcpy

fc = r"F:\GIS\ParcelUpdate\2018_10\Workspace\ParcelUpdate_Workspace.gdb\Parcel_Master_New" 
new_fc = r"F:\GIS\ParcelUpdate\2018_10\Workspace\ParcelUpdate_Workspace.gdb\Parcel_Master" 

field_mappings = arcpy.FieldMappings() # Create new field mapping object

#Loop through fields. For each field, create a corresponding FieldMap object.
#If the name ends with "_NEW", strip it off.
#Note: "FID and "Shape" are skipped

for field in arcpy.ListFields(fc):
    if not field.name == "OBJECTID" and not field.name == "Shape":
        old_name = field.name

        #Rename if necessary
        if old_name.endswith("_NEW"):
            new_name = old_name[:-4]
        else:
            new_name = old_name

        #Create new FieldMap object    
        new_f = arcpy.FieldMap()
        new_f.addInputField(fc, old_name) # Specify the input field to use

        #Rename output field
        new_f_name = new_f.outputField
        new_f_name.name = new_name
        new_f_name.aliasName = new_name
        new_f.outputField = new_f_name

        #Add field to FieldMappings object
        field_mappings.addFieldMap(new_f)

#Convert table using your created Field Mappings object
arcpy.FeatureClassToFeatureClass_conversion(fc, os.path.dirname(new_fc), os.path.basename(new_fc), field_mapping=field_mappings)

<Result 'F:\\GIS\\ParcelUpdate\\2018_10\\Workspace\\ParcelUpdate_Workspace.gdb\\Parcel_Master'>

## Perform Spatial Joins and Update Parcel Fields

### Field Calculator Function

In [20]:
import arcpy

def fieldJoinCalc(updateFC, updateFieldsList, sourceFC, sourceFieldsList):
    from time import strftime  
    print ("Started calculation: " + strftime("%Y-%m-%d %H:%M:%S"))
    
    #updateFC = r"C:\Path\UpdateFeatureClass"  
    #updateFieldsList = ["JoinField", "ValueField"]
    
    # sourceFC = r"C:\Path\SourceFeatureClass"  
    #sourceFieldsList = ["JoinField", "ValueField"]  
    
    # Use list comprehension to build a dictionary from a da SearchCursor  
    valueDict = {r[0]:(r[1:]) for r in arcpy.da.SearchCursor(sourceFC, sourceFieldsList)}  
   
    with arcpy.da.UpdateCursor(updateFC, updateFieldsList) as updateRows:  
        for updateRow in updateRows:  
            # store the Join value of the row being updated in a keyValue variable  
            keyValue = updateRow[0]  
            # verify that the keyValue is in the Dictionary  
            if keyValue in valueDict:  
                # transfer the value stored under the keyValue from the dictionary to the updated field.  
                updateRow[1] = valueDict[keyValue][0]  
                updateRows.updateRow(updateRow)    
    del valueDict  
    print ("Finished calculation: " + strftime("%Y-%m-%d %H:%M:%S"))

### Set local variables

In [21]:
import arcpy

ParcelLayer = "C:\\GIS\\PROJECT\\2018_10\\Workspace\\ParcelUpdate_Workspace.gdb\\Parcel_Master_1"
ParcelPoint = "C:\\GIS\\PROJECT\\2018_10\\Workspace\\ParcelUpdate_Workspace.gdb\\Parcel_Point"

if arcpy.Exists(ParcelPoint):
    arcpy.Delete_management(ParcelPoint)
arcpy.FeatureToPoint_management(ParcelLayer, ParcelPoint, "INSIDE")

# SDE feature classes from C: drive
# sde_FireDistrict = "C:\\GIS\\PROJECT\\SDE\\SDE_Archive_2018.gdb\\Jurisdictions\\FireDistricts"

# File paths
sdeBase = "F:\\GIS\\GIS_DATA\\Vector.sde"
#sde feature classes
sde_FireDistrict = sdeBase + "\\sde.SDE.Jurisdictions\\sde.SDE.FireDistricts"
sde_NRCSSoils1974 = sdeBase + "\\sde.SDE.Soils\\sde.SDE.NRCS_Soils_1974"
sde_NRCSSoils2003 = sdeBase + "\\sde.SDE.Soils\\sde.SDE.NRCS_Soils_2003"
sde_HydroArea = sdeBase + "\\sde.SDE.Water\\sde.SDE.Hydro_Areas"
sde_Watershed = sdeBase + "\\sde.SDE.Water\\sde.SDE.Priority"
sde_RegionalLandUse = sdeBase + "\\sde.SDE.Planning\\sde.SDE.RegionalLandUse"
sde_LocalPlan = sdeBase + "\\sde.SDE.Planning\\sde.SDE.LocalPlan"
sde_Zoning =  sdeBase + "\\sde.SDE.Planning\\sde.SDE.Zoning_LocalPlan"
sde_SpecialDistrict = sdeBase + "\\sde.SDE.Planning\\sde.SDE.SpecialPlanningDistrict"
sde_TownCenter = sdeBase + "\\sde.SDE.Planning\\sde.SDE.TownCenter"
sde_TownCenterBuffer = sdeBase + "\\sde.SDE.Planning\\sde.SDE.TownCenter_Buffer"
sde_Index1987 = sdeBase + "\\sde.SDE.Planning\\sde.SDE.AssessorMapIndex_1987"
sde_TRPAboundary = sdeBase + "\\sde.SDE.Jurisdictions\\sde.SDE.TRPA_bdy"
sde_UrbanArea = sdeBase + "\\sde.SDE.Jurisdictions\\sde.SDE.UrbanAreas"
sde_Zip = sdeBase + "\\sde.SDE.Census\\sde.SDE.Tahoe_Census_Zip"

# in memory files
wk_memory = "in_memory" + "\\"
ParcelPoint_FireDistrict = wk_memory + "ParcelPoint_FireDistrict"
ParcelPoint_Soils74 = wk_memory + "\\ParcelPoint_Soils74"
ParcelPoint_Soils03 = wk_memory + "\\ParcelPoint_Soils03"
ParcelPoint_HydroArea = wk_memory + "\\ParcelPoint_HydroArea"
ParcelPoint_Watershed = wk_memory + "\\ParcelPoint_Watershed"
ParcelPoint_RegionalLandUse = wk_memory + "\\ParcelPoint_RegionalLandUse"
ParcelPoint_LocalPlan = wk_memory + "\\ParcelPoint_LocalPlan"
ParcelPoint_TownCenter = wk_memory + "\\ParcelPoint_TownCenter"
ParcelPoint_TownCenterBuffer = wk_memory + "\\ParcelPoint_TownCenterBuffer"
ParcelPoint_Zoning = wk_memory + "\\ParcelPoint_Zoning"
ParcelPoint_SpecialDistrict = wk_memory + "\\ParcelPoint_SpecialDistrict"
ParcelPoint_Index1987 = wk_memory + "\\ParcelPoint_Index1987"
ParcelPoint_PstlTown = wk_memory + "\\ParcelPoint_PstlTown"
ParcelPoint_PstlZip = wk_memory + "\\ParcelPoint_PstlZip"

Starting the Fire District Spatial Join
Finished the Fire District Spatial Join
Start calculation: 2018-11-07 20:38:45
Finished calculation: 2018-11-07 20:38:48
The 'FIREPD' field has been updated


### Update Fire Protection District

In [ ]:
# delete feature class if it exists already
if arcpy.Exists(ParcelPoint_FireDistrict):
    arcpy.Delete_management(ParcelPoint_FireDistrict)

print("Starting the Fire District Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_FireDistrict, ParcelPoint_FireDistrict, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Fire District Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'FIREPD'], ParcelPoint_FireDistrict, ['APN', 'DISTRICT'])
print ("The 'FIREPD' field in the parcel data has been updated")

### Update Soils 1974 Field

In [ ]:
# delete feature class if it exists already
if arcpy.Exists(ParcelPoint_Soils74):
    arcpy.Delete_management(ParcelPoint_Soils74)

print("Starting the SOIL_1974 Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_NRCSSoils1974, ParcelPoint_Soils74, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the SOIL_1974 Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'SOIL_1974'], ParcelPoint_Soils74, ['APN', 'MUSYM_74'])
print ("The 'SOIL_1974' field in the parcel data has been updated")

### Update Soils 2003 Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_Soils03):
    arcpy.Delete_management(ParcelPoint_Soils03)

print("Starting the SOIL_2003 Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_NRCSSoils2003, ParcelPoint_Soils03, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the SOIL_2003 Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'SOIL_2003'], ParcelPoint_Soils03, ['APN', 'MUSYM_03'])
print ("The 'SOIL_2003' field in the parcel data has been updated")

### Update Hydrologic Area Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_HydroArea):
    arcpy.Delete_management(ParcelPoint_HydroArea)

print("Starting the Hyrdrologic Area Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_HydroArea, ParcelPoint_HydroArea, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Hydrologic Area Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'HRA_NAME'], ParcelPoint_HydroArea, ['APN', 'HRA_NAME'])
print ("The 'HRA_NAME' field in the parcel data has been updated")

### Update Watershed Fields

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_Watershed):
    arcpy.Delete_management(ParcelPoint_Watershed)

print("Starting the Watershed Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_Watershed, ParcelPoint_Watershed, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Watershed Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'WATERSHED_NUMBER'], ParcelPoint_Watershed, ['APN', 'NUMBER_'])
print ("The 'WATERSHED_NUMBER' field in the parcel data has been updated")
fieldJoinCalc(ParcelLayer, ['APN', 'WATERSHED_NAME'], ParcelPoint_Watershed, ['APN', 'NAME'])
print ("The 'WATERSHED_NAME' field in the parcel data has been updated")
fieldJoinCalc(ParcelLayer, ['APN', 'PRIORITY_WATERSHED'], ParcelPoint_Watershed, ['APN', 'PRIORITY'])
print ("The 'PRIORITY_WATERSHED' field in the parcel data has been updated")

### Update Regional Land Use Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_RegionalLandUse):
    arcpy.Delete_management(ParcelPoint_RegionalLandUse)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_RegionalLandUse, ParcelPoint_RegionalLandUse, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'REGIONAL_LANDUSE'], ParcelPoint_RegionalLandUse, ['APN', 'Description'])
print ("The 'REGIONAL_LANDUSE' field in the parcel data has been updated")

### Update Local Plan Fields

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_NAME'], ParcelPoint_LocalPlan, ['APN', 'PLAN_NAME'])
print ("The 'PAS_NAME' field in the parcel data has been updated")
fieldJoinCalc(ParcelLayer, ['APN', 'LOCAL_PLAN_HYPERLINK'], ParcelPoint_LocalPlan, ['APN', 'File_URL'])
print ("The 'LOCAL_PLAN_HYPERLINK' field in the parcel data has been updated")

### Update Town Center Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_TownCenter):
    arcpy.Delete_management(ParcelPoint_TownCenter)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_TownCenter, ParcelPoint_TownCenter, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'TownCenter'], ParcelPoint_TownCenter, ['APN', 'NAME'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update Town Center Buffer Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update Zoning Fields

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update Special District Fields

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update 1987 Index Fields

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update Postal Town Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update Postal Zip Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update Within TRPA Boundary Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update Littoral Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update Allowed Coverage Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update Impervious Coverage Field

In [ ]:
# delete in memory output feature class if it exists already
if arcpy.Exists(ParcelPoint_LocalPlan):
    arcpy.Delete_management(ParcelPoint_LocalPlan)

print("Starting the Regional Land Use Spatial Join")
# Process Fire District Spatial Join
arcpy.SpatialJoin_analysis(ParcelPoint, sde_LocalPlan, ParcelPoint_LocalPlan, "JOIN_ONE_TO_ONE", "KEEP_ALL", "", "HAVE_THEIR_CENTER_IN", "", "")
print ("Finished the Regional Land Use Spatial Join")

# transfer attributes to Parcel Layer
fieldJoinCalc(ParcelLayer, ['APN', 'PAS_ID'], ParcelPoint_LocalPlan, ['APN', 'PLAN_ID'])
print ("The 'PAS_ID' field in the parcel data has been updated")

### Update Land Use fields

In [63]:
import arcpy

fc = r"F:\GIS\ParcelUpdate\2018_10\Workspace\ParcelUpdate_Workspace.gdb\Parcel_Master"
fields = ("COUNTY_LANDUSE", "COUNTY_LANDUSE_DESCRIPTION", "TRPA_LANDUSE_DESCRIPTION", 'JURISDICTION')

with arcpy.da.UpdateCursor(fc, fields) as cursor:
    for row in cursor:
        ctyluc = row[0]
        cty = row[3]
# set Washoe county land use code
        # set TRPA Land Use Description
        if (row[0] != None or row[0] != "") and (row[3] == 'WA'):
            if ctyluc in ('400', '410', '440', '500', '510', '520', '630', '640', '670', '720'):
                row[2] = "Commercial"
            elif ctyluc in ('210', '250'):
                row[2] = "Condominium"
            elif ctyluc in ('240'):
                row[2] = "Condominium Common Area"
            elif ctyluc in ('220', '230', '300', '310', '320', '330', '340', '350', '360'):
                row[2] = "Multi-Family Residential"
            elif ctyluc in ('600', '620'):
                row[2] = "Open Space"
            elif ctyluc in ('700', '710', 'PBRD'):
                row[2] = "Public Service"
            elif ctyluc in ('190'):
                row[2] = "Recreation"
            elif ctyluc in ('200'):
                row[2] = "Single Family Residential"     
            elif ctyluc in ('420', '430'):
                row[2] = "Tourist Accommodation"
            elif ctyluc in ('100', '110', '120', '130', '140', '150', '160', '170', '180'):
                row[2] = "Vacant"            

        cursor.updateRow(row)
        # set county land use description field
        if (row[0] != None or row[0] != "") and (row[3] == 'WA'):
            if ctyluc in ('710'):
                row[1] = "Intracounty public utility"
            elif ctyluc == '700':
                row[1] = 'Centrally assessed public utility'
            elif ctyluc == '510':
                row[1] = 'Commercial Industrial: retail or office with Indus'
            elif ctyluc == '500':
                row[1] = 'General industrial: light indust, trucking, warehs'
            elif ctyluc == '440':
                row[1] = 'Resort commercial: ski, golf, sports, etc.'
            elif ctyluc == '430':
                row[1] = 'Commercial hotel or motel'
            elif ctyluc == '420':
                row[1] = 'Casino or hotel casino'
            elif ctyluc == '410':
                row[1] = 'Offices, professional and business, banks, etc.'
            elif ctyluc == '400':
                row[1] = 'General Commercial: retail, mixed, parking, school'
            elif ctyluc == '340':
                row[1] = 'Ten or more units'
            elif ctyluc == '330':
                row[1] = 'Five to Nine Units'
            elif ctyluc == '320':
                row[1] = 'Three or four Units'
            elif ctyluc == '310':
                row[1] = 'Two Single Family Units'
            elif ctyluc == '300':
                row[1] = 'Duplex'
            elif ctyluc == '250':
                row[1] = 'Condo or Townhouse valued as apartment use'
            elif ctyluc == '240':
                row[1] = 'Common Area'
            elif ctyluc == '210':
                row[1] = 'Condominium or Townhouse'
            elif ctyluc == '200':
                row[1] = 'Single Family Residence'
            elif ctyluc == '190':
                row[1] = 'Public Parks: vacant or improved'
            elif ctyluc == '170':
                row[1] = 'Other, unbuildable: roads, restrictions, terrain'
            elif ctyluc == '160':
                row[1] = 'Splinter, unbuildable: small size or shape'
            elif ctyluc == '140':
                row[1] = 'Vacant, commercial'
            elif ctyluc == '130':
                row[1] = 'Vacant, multi-residential'
            elif ctyluc == '120':
                row[1] = 'Vacant, single family'
            elif ctyluc == '110':
                row[1] = 'Vacant, under development'
            elif ctyluc == '100':
                row[1] = 'Vacant, other or unknown'            

        cursor.updateRow(row)
# Set Carson City County Land Use Descriptions
        # set TRPA land use description
        if (row[0] != None or row[0] != "") and (row[3] == 'CC'):
            if ctyluc in ('400', '401', '402', '403', '404', '408', '410', '411', 
                          '412', '440', '441', '460', '470', '480', '482', '490', 
                          '500', '501', '510', '511', '512', '513', '520', '521', 
                          '560', '570', '580', '582', '590', '624', '625', '694', 
                          '800', '820', '830', '840', '880', '882', '890', '920', 
                          '921', '930', '960', '980', '990'):
                row[2] = "Commercial"
            elif ctyluc in ('210', '211'):
                trpalucdesc = "Condominium"
            elif ctyluc == '970':
                row[2] = "Condominium Common Area"
            elif ctyluc in ('240', '241', '300', '301', '310', '311', '313', '320', 
                            '321', '330', '331', '333', '340', '341', '350', '360', 
                            '370', '380', '382', '390', '698'):
                row[2] = "Multi-Family Residential"
            elif ctyluc in ('190', '600', '610', '612', '613', '614', '615', '616', 
                            '618', '620', '695', '696', '697', '810'):
                row[2] = "Open Space"
            elif ctyluc in ('700', '710', '711', '720', '731', '732', '733', '780', 
                            '790', '910', '922'):
                row[2] = "Public Service"
            elif ctyluc in ('450', '900'):
                row[2] = "Recreation"
            elif ctyluc in ('200', '201', '220', '222', '230', '231', '232', '260', 
                            '270', '280', '282', '290', '622', '692', '693'):
                row[2] = "Single Family Residential"     
            elif ctyluc in ('420', '421', '430', '431', '432', '514'):
                row[2] = "Tourist Accommodation"
            elif ctyluc in ('100', '108', '110', '117', '120', '130', '140', '150', '160'):
                row[2] = "Vacant"

        cursor.updateRow(row)
        # set county LUC Description
        if (row[0] != None or row[0] != "") and (row[3] == 'CC'):
            if ctyluc == '980':
                row[1] = 'Special Purpose with Minor Improvements'
            elif ctyluc == '320':
                row[1] = 'Three to Four Units'
            elif ctyluc == '280':
                row[1] = 'Single Family Residential with Minor Improvements'
            elif ctyluc == '190':
                row[1] = 'Vacant - Public Use Lands'
            elif ctyluc == '120':
                row[1] = 'Vacant - Single Family Residential' 

        cursor.updateRow(row)
# update Douglas Land Use descriptions        
        #Update TRPA Land Use description
        if (row[0] != None or row[0] != "") and (row[3] == 'DG'):
            if ctyluc in ('400', '402', '410', '411', '412', 
                          '440', '460', '470', '480', '500', 
                          '510', '560', '580', '582'):
                row[2] = "Commercial"
            elif ctyluc in ('210', '211'):
                row[2] = "Condominium"
            elif ctyluc == '270':
                row[2] = "Condominium Common Area"
            elif ctyluc in ('300', '310', '320', '330', '350', '390'):
                row[2] = "Multi-Family Residential"
            elif ctyluc == '190':
                row[2] = "Open Space"
            elif ctyluc in ('700', '710', '711', '910', '980', '970'):
                row[2] = "Public Service"
            elif ctyluc in ('450', '900', '970'):
                row[2] = "Recreation"
            elif ctyluc in ('200', '220', '230', '236', '240', '280', '282'):
                row[2] = "Single Family Residential"     
            elif ctyluc in ('420', '430'):
                row[2] = "Tourist Accommodation"
            elif ctyluc in ('100', '110', '117', '120', '130', '140'):
                row[2] = "Vacant"

        cursor.updateRow(row)
        if (row[0] != None or row[0] != "" or ctyluc.isspace() != True) and (row[3] == 'DG'):
            # set County land use description
            if ctyluc == '980':
                row[1] = 'Special Purpose with Minor Improvements'
            elif ctyluc == '970':
                row[1] = 'Special Purpose Common Area'
            elif ctyluc == '910':
                row[1] = 'Cemeteries'
            elif ctyluc == '900':
                row[1] = 'Parks for Public Use'
            elif ctyluc == '711':
                row[1] = 'Communication, Transportation, and Utility Property of a Local Nature Under Construction'
            elif ctyluc == '710':
                row[1] = 'Communication, Transportation, and Utility Property of a Local Nature'
            elif ctyluc == '700':
                row[1] = 'Operating Communication, Transportation, and Utility Property of an Interstate or Intercounty Nature'
            elif ctyluc == '582':
                row[1] = 'Industrial with Minor Improvements - with structures insufficient to determine intended use'
            elif ctyluc == '580':
                row[1] = 'Industrial with Minor Improvements'
            elif ctyluc == '560':
                row[1] = 'Industrial Auxiliary Area'
            elif ctyluc == '510':
                row[1] = 'Commercial Industrial - retail or office use combined with Industrial use'
            elif ctyluc == '500':
                row[1] = 'General Industrial - light industry, trucking and warehousing, service, repair, etc.'
            elif ctyluc == '480':
                row[1] = 'Commercial with Minor Improvements'
            elif ctyluc == '470':
                row[1] = 'Commercial Common Area'
            elif ctyluc == '460':
                row[1] = 'Commercial Auxiliary Area'
            elif ctyluc == '450':
                row[1] = 'Golf Course'
            elif ctyluc == '440':
                row[1] = 'Commercial Recreation'
            elif ctyluc == '430':
                row[1] = 'Commercial Living Accommodations'
            elif ctyluc == '420':
                row[1] = 'Casino or Hotel Casino'
            elif ctyluc == '410':
                row[1] = 'Offices, Professional and Business Services'
            elif ctyluc == '402':
                row[1] = 'Parking and/or Parking Structures'
            elif ctyluc == '400':
                row[1] = 'General Commercial'
            elif ctyluc == '390':
                row[1] = 'Mixed Use with Multi-Family Residential as primary use'
            elif ctyluc == '350':
                row[1] = 'Manufactured Home Park - Ten or More Manufactured Home Units'
            elif ctyluc == '330':
                row[1] = 'Five or More Units - Low Rise'
            elif ctyluc == '320':
                row[1] = 'Three to Four Units'
            elif ctyluc == '310':
                row[1] = 'Two Single Family Units'
            elif ctyluc == '300':
                row[1] = 'Duplex'
            elif ctyluc == '282':
                row[1] = 'Single Family Residential with Minor Improvements - No livable structures'
            elif ctyluc == '280':
                row[1] = 'Single Family Residential with Minor Improvements'
            elif ctyluc == '270':
                row[1] = 'Single Family Residential Common Area'
            elif ctyluc == '240':
                row[1] = 'Individual Residential Unit - Townhouse or Row House'
            elif ctyluc == '236':
                row[1] = 'Personal Property Manufactured Home Secured'
            elif ctyluc == '230':
                row[1] = 'Personal Property Manufactured Home on the Unsecured Roll'
            elif ctyluc == '220':
                row[1] = 'Manufactured Home Converted to Real Property'
            elif ctyluc == '210':
                row[1] = 'Individual Unit in a Multiple Unit Building'
            elif ctyluc == '200':
                row[1] = 'Single Family Residence'
            elif ctyluc == '190':
                row[1] = 'Vacant - Public Use Lands'
            elif ctyluc == '140':
                row[1] = 'Vacant - Commercial'
            elif ctyluc == '130':
                row[1] = 'Vacant - Multi-Residential'
            elif ctyluc == '120':
                row[1] = 'Vacant - Single Family Residential'
            elif ctyluc == '117':
                row[1] = 'Vacant - Roads/Easements'
            elif ctyluc == '110':
                row[1] = 'Vacant - Splinter and Other Unbuildable'
            elif ctyluc == '100':
                row[1] = 'Vacant - Unknown/Other'
        cursor.updateRow(row)
# Set El Doroda County Land Use Descrition fields
        if (row[0] != None or row[0] != "") and (row[3] == 'EL'):
            if ctyluc in ('03', '29', '31', '32', '34', '36', '37', '38', '39', '41', '42', '43', '44', '45', '46', '47', '48', 
                          '65', '67', '68', '82', '91', '93'):
                row[2] = "Commercial"
            elif ctyluc == '14':
                row[2] = "Condominium"
            elif ctyluc == '89':
                row[2] = "Condominium Common Area"
            elif ctyluc in ('01', '07', '12', '13', '16', '18', '19', '28', '35'):
                row[2] = "Multi-Family Residential"
            elif ctyluc in ('25', '26', '50', '51', '52', '55', '56', '60', '70', '75', '79'):
                row[2] = "Open Space"
            elif ctyluc in ('90', '92', '94', '96', '97', '98'):
                row[2] = "Public Service"
            elif ctyluc in ('61', '62', '63', '64'):
                row[2] = "Recreation"
            elif ctyluc in ('06', '11', '15', '22', '23'):
                row[2] = "Single Family Residential"     
            elif ctyluc in ('33', '80', '81'):
                row[2] = "Tourist Accommodation"
            elif ctyluc in ('00', '02', '05', '17', '21', '24', '30', '40'):
                row[2] = "Vacant"
            elif ctyluc is None:
                row[2] == ''
        cursor.updateRow(row)
# set county land use description
        if (row[0] != None or row[0] != "") and (row[3] == 'EL'):
            if ctyluc == '98':
                row[1] = 'DEV MSC FIRE SUPPRESSION FACILITIES'
            elif ctyluc == '96':
                row[1] = 'DEV MSC CEMETERIES'
            elif ctyluc == '94':
                row[1] = 'DEV MSC SCHOOLS - LARGE (101+ STUDENTS)'
            elif ctyluc == '93':
                row[1] = 'DEV MSC SCHOOLS - MEDIUM (13-100 STUDENTS)'
            elif ctyluc == '92':
                row[1] = 'DEV MSC SCHOOLS - SMALL (1-12 STUDENTS)'
            elif ctyluc == '90':
                row[1] = 'UTL IND PUBLIC UTILITY (ON STATE ASSESSED ROLL)'
            elif ctyluc == '84':
                row[1] = 'DEV MSC TEMPORARY USE CODE FOR PROJECT 184'
            elif ctyluc == '82':
                row[1] = 'DEV COM PARKING LOT'
            elif ctyluc == '81':
                row[1] = 'DEV MSC UNDERLYING INTEREST IN TIME SHARE PROJ'
            elif ctyluc == '79':
                row[1] = 'RLU MSC ENV. SENSITIVE LAND - RESTRICTED USE'
            elif ctyluc == '68':
                row[1] = 'DEV COM MARINAS'
            elif ctyluc == '65':
                row[1] = 'DEV COM RESTAURANT'
            elif ctyluc == '64':
                row[1] = 'DEV MSC SKI RESORTS'
            elif ctyluc == '63':
                row[1] = 'DEV MSC CAMPGROUNDS'
            elif ctyluc == '62':
                row[1] = 'DEV MSC COMMUNITY ORIENTED FACILITIES'
            elif ctyluc == '61':
                row[1] = 'DEV MSC MISC. IMPROVED RECREATIONAL'
            elif ctyluc == '60':
                row[1] = 'VAC MSC VACANT RECREATIONAL LAND'
            elif ctyluc == '50':
                row[1] = 'TPZ MSC TIMBER PRESERVE ZONING - ACTIVE'
            elif ctyluc == '48':
                row[1] = 'DEV IND OFFICES'
            elif ctyluc == '47':
                row[1] = 'DEV IND HOSPITALS & CONVALESCENT HOSPITALS'
            elif ctyluc == '46':
                row[1] = 'DEV IND MEDICAL/DENTAL/VET OFFICES'
            elif ctyluc == '45':
                row[1] = 'DEV IND LIGHT MANUFACTURING'
            elif ctyluc == '43':
                row[1] = 'DEV IND WAREHOUSES'
            elif ctyluc == '42':
                row[1] = 'DEV IND MINI-WAREHOUSES (MINI-STORAGE)'
            elif ctyluc == '41':
                row[1] = 'DEV IND MISC. IMPROVED INDUSTRIAL PROPERTY'
            elif ctyluc == '40':
                row[1] = 'VAC IND VACANT INDUSTRIAL LAND'
            elif ctyluc == '39':
                row[1] = 'DEV COM SUPERMARKETS'
            elif ctyluc == '38':
                row[1] = 'DEV COM RETAIL STORES >15,000 SQ. FT.'
            elif ctyluc == '37':
                row[1] = 'DEV COM RETAIL STORES 5,001-15,000 SQ. FT.'
            elif ctyluc == '36':
                row[1] = 'DEV COM RETAIL STORES <=5,000 SQ. FT.'
            elif ctyluc == '35':
                row[1] = 'DEV COM MOBILE HOME PARKS'
            elif ctyluc == '34':
                row[1] = 'DEV COM SERVICE STATION'
            elif ctyluc == '33':
                row[1] = 'DEV COM MOTEL, HOTEL'
            elif ctyluc == '31':
                row[1] = 'DEV COM MISC. IMPROVED COMMERCIAL'
            elif ctyluc == '30':
                row[1] = 'VAC COM VACANT COMMERCIAL LAND'
            elif ctyluc == '29':
                row[1] = 'DEV MSC RURAL NON-RES. IMPROVEMENT 2.51-20.0 AC.'
            elif ctyluc == '26':
                row[1] = 'AGP MSC RURAL RESTRICTIVE ZONING - NON-RENEWAL'
            elif ctyluc == '25':
                row[1] = 'AGP MSC RURAL RESTRICTIVE ZONING - CLCA (ACTIVE)'
            elif ctyluc == '24':
                row[1] = 'VAC RES RURAL RES. LAND 20+ MINOR NON-RES IMPR'
            elif ctyluc == '23':
                row[1] = 'DEV RES RURAL RES. 20+ AC. 1 RES. UNIT'
            elif ctyluc == '22':
                row[1] = 'DEV RES RURAL RES. 2.51-20.0 AC. 1 SF UNIT'
            elif ctyluc == '21':
                row[1] = 'VAC RES VAC RURAL RES LAND 2.51-20.0 AC. 1 UNIT'
            elif ctyluc == '17':
                row[1] = 'VAC MSC SUBJ. TO OPEN SPACE CONTRACT (NOT CLCA)'
            elif ctyluc == '16':
                row[1] = 'DEV RES MOBILE HOME ON RENTED LAND'
            elif ctyluc == '15':
                row[1] = 'DEV RES RESIDENCE ON LEASED LAND'
            elif ctyluc == '14':
                row[1] = 'DEV MFR CONDOMINIUMS & TOWNHOUSES'
            elif ctyluc == '13':
                row[1] = 'DEV MFR MULTI-RESIDENTIAL 4+ UNITS'
            elif ctyluc == '12':
                row[1] = 'DEV MFR MULTI-RESIDENTIAL 2-3 UNITS'
            elif ctyluc == '11':
                row[1] = 'DEV RES SINGLE FAM. RES. <=2.5 AC.(INC. MAN. HMS'
            elif ctyluc == '07':
                row[1] = 'DEV MFR RETIREMENT HOUSING'
            elif ctyluc == '05':
                row[1] = 'VAC MFR VACANT MULTI-RES. LAND 4+ UNITS ALLOWED'
            elif ctyluc == '03':
                row[1] = 'DEV COM PLACE OF WORSHIP'
            elif ctyluc == '02':
                row[1] = 'VAC RES NON-RES. IMPROVEMENTS <=2.5 AC.'
            elif ctyluc == '00':
                row[1] = 'VAC RES VACANT RES. LAND <=2.5 AC. 1-3 UNITS'

        cursor.updateRow(row)

# set TRPA land use description
        if (row[0] != None or row[0] != "") and (row[3] == 'PL'):
            if ctyluc in ('07', '11', '12', '13', '14', '15', '17', '21', '22', '23', 
                          '24', '25', '26', '27', '29', '31', '32', '36', '37', '38', 
                          '39', '62', '63', '71', '88'):
                row[2] = "Commercial"
            elif ctyluc == '04':
                row[2] = "Condominium"
            elif ctyluc == '89':
                row[2] = "Condominium Common Area"
            elif ctyluc in ('02', '03', '04', '05', '09', '28'):
                row[2] = "Multi-Family Residential"
            elif ctyluc in ('56', '60', '87', '90'):
                row[2] = "Open Space"
            elif ctyluc in ('72', '76', '77', '81'):
                row[2] = "Public Service"
            elif ctyluc in ('65', '66', '67', '68', '69'):
                row[2] = "Recreation"
            elif ctyluc in ('01', '08', '16'):
                row[2] = "Single Family Residential"     
            elif ctyluc in ('06', '18', '64'):
                row[2] = "Tourist Accommodation"
            elif ctyluc in ('00', '10', '20', '30'):
                row[2] = "Vacant"

        cursor.updateRow(row)
# set Placer county land use description 
        if (row[0] != None or row[0] != "") and (row[3] == 'PL'):
            # set county land use description
            if ctyluc == '90':
                row[1] = 'GREENBELT'
            elif ctyluc == '89':
                row[1] = 'COMMON AREA'
            elif ctyluc == '88':
                row[1] = 'HIGHWAYS, ROADS, STREETS'
            elif ctyluc == '87':
                row[1] = 'RIVERS, LAKES, RESERVOIR, CANAL'
            elif ctyluc == '81':
                row[1] = 'UTILITIES, PUBLIC & PRIVATE'
            elif ctyluc == '77':
                row[1] = 'CEMETERIES'
            elif ctyluc == '76':
                row[1] = 'MISC. PUBLIC BUILDINGS'
            elif ctyluc == '72':
                row[1] = 'SCHOOLS'
            elif ctyluc == '71':
                row[1] = 'CHURCHES'
            elif ctyluc == '69':
                row[1] = 'MISCELLANEOUS RECREATIONAL'
            elif ctyluc == '68':
                row[1] = 'CAMPS & PARKS, GENERAL'
            elif ctyluc == '67':
                row[1] = 'SKI FACILITY'
            elif ctyluc == '66':
                row[1] = 'GOLF COURSE'
            elif ctyluc == '65':
                row[1] = 'TENNIS, SWIMMING CLUBS'
            elif ctyluc == '64':
                row[1] = 'LODGES, HALLS'
            elif ctyluc == '63':
                row[1] = 'MARINA, PIER'
            elif ctyluc == '62':
                row[1] = 'THEATER, BOWLING ALLEY'
            elif ctyluc == '61':
                row[1] = 'NON-PROFIT CAMPS/PARKS'
            elif ctyluc == '60':
                row[1] = 'CONSERVATION EASEMENT RESTRICTIONS'
            elif ctyluc == '56':
                row[1] = 'TIMBERLAND, ZONED TPZ'
            elif ctyluc == '55':
                row[1] = 'TIMBERLAND, UNRESTRICTED'
            elif ctyluc == '39':
                row[1] = 'MISCELLANEOUS INDUSTRIAL'
            elif ctyluc == '38':
                row[1] = 'WAREHOUSE'
            elif ctyluc == '37':
                row[1] = 'MINI-STORAGE, COVERED STORAGE'
            elif ctyluc == '36':
                row[1] = 'UNCOVERED STORAGE, WRECKING YARD'
            elif ctyluc == '32':
                row[1] = 'HEAVY INDUSTRIAL'
            elif ctyluc == '31':
                row[1] = 'LIGHT INDUSTRIAL'
            elif ctyluc == '30':
                row[1] = 'VACANT INDUSTRIAL'
            elif ctyluc == '29':
                row[1] = "MISCELLANEOUS COMM'L"
            elif ctyluc == '28':
                row[1] = 'MOBILE HOME PARK'
            elif ctyluc == '27':
                row[1] = 'PARKING LOTS'
            elif ctyluc == '26':
                row[1] = 'AUTO SALES, REPAIR'
            elif ctyluc == '25':
                row[1] = 'SERVICE STATION'
            elif ctyluc == '24':
                row[1] = 'MINI-MARKET WITH GAS'
            elif ctyluc == '23':
                row[1] = "BANKS, S&L'S, CREDIT UNION"
            elif ctyluc == '22':
                row[1] = 'FAST FOOD RESTAURANT'
            elif ctyluc == '21':
                row[1] = 'RESTAURANTS, COCKTAIL LOUNGES'
            elif ctyluc == '20':
                row[1] = 'VACANT, COMMERCIAL'
            elif ctyluc == '19':
                row[1] = 'OFFICE MEDICAL/DENTAL'
            elif ctyluc == '18':
                row[1] = 'HOTELS, MOTELS, RESORTS'
            elif ctyluc == '17':
                row[1] = 'OFFICE GENERAL'
            elif ctyluc == '16':
                row[1] = 'RESIDENCE ON COMMERCIAL LAND'
            elif ctyluc == '15':
                row[1] = 'SHOPPING CENTER'
            elif ctyluc == '14':
                row[1] = 'OFFICE CONDO'
            elif ctyluc == '13':
                row[1] = 'MINI-MARKETS, NO GAS'
            elif ctyluc == '12':
                row[1] = 'SUBURBAN STORE'
            elif ctyluc == '11':
                row[1] = 'COMMERCIAL STORE'
            elif ctyluc == '10':
                row[1] = 'VACANT, SUBDIVIDED RESIDENTIAL'
            elif ctyluc == '09':
                row[1] = 'MOBILE HOME IN M H PARK'
            elif ctyluc == '08':
                row[1] = 'MOBILE HOME OUTSIDE OF PARK'
            elif ctyluc == '07':
                row[1] = 'RESIDENTIAL, AUXILIARY IMP'
            elif ctyluc == '06':
                row[1] = 'TIMESHARES'
            elif ctyluc == '05':
                row[1] = 'APARTMENTS, 4 UNITS OR MORE'
            elif ctyluc == '04':
                row[1] = 'SINGLE FAM RES, CONDO'
            elif ctyluc == '03':
                row[1] = '3 SINGLE FAM RES, TRIPLEX'
            elif ctyluc == '02':
                row[1] = '2 SINGLE FAM RES, DUPLEX'
            elif ctyluc == '01':
                row[1] = 'SINGLE FAM RES, HALF PLEX'
            elif ctyluc == '00':
                row[1] = 'VACANT, ALL TYPES-NOT ASGND'

        cursor.updateRow(row)
    print ("Updated Land Use Description fields.")

Updated Land Use Description fields.


### Update Parcel Point

In [3]:
import arcpy
import os
from datetime import datetime

workspace = "C:\\GIS\\PROJECT\\SDE\\SDE_Archive_2018.gdb"

inputFC = "C:\\GIS/PROJECT\\ParcelUpdate_Dev\\Parcel_NewData.gdb\\Parcel_Point"

outputFC = "C:\\GIS\\PROJECT\\SDE\\SDE_Archive_2018.gdb\\Parcels\\ParcelPoints"

fields = ['APN', 'PPNO', 'JURISDICTION', 'PARCEL_ACRES', 'PARCEL_SQFT', 'SHAPE@XY']

# Start an edit session. Must provide the workspace.
#edit = arcpy.da.Editor(workspace)

# Edit session is started without an undo/redo stack for versioned data
#  (for second argument, use False for unversioned data)
#edit.startEditing(False, True)

# delete rows in sde feature class
daDeleteStart = datetime.now()

# Start an edit operation
#edit.startOperation()
with arcpy.da.UpdateCursor(outputFC, fields) as dCursor:
    for row in dCursor:
        dCursor.deleteRow()
        print("Record deleted: {}".format(row[0]))
# Stop the edit operation.
#edit.stopOperation()

daDeleteEnd = datetime.now() - daDeleteStart
print ("Time it took to delete rows: {}".format(daDeleteEnd))

# insert rows from staging feature class into SDE feature class
daInsertStart = datetime.now()
# Start an edit operation
#edit.startOperation()
with arcpy.da.InsertCursor(outputFC, fields) as iCursor:
    with arcpy.da.SearchCursor(inputFC, fields) as sCursor:
        for row in sCursor:
            iCursor.insertRow(row)
            print("Record added: {}".format(row[0]))
# Stop the edit operation.
#edit.stopOperation()

daInsertEnd = datetime.now() - daInsertStart

# Stop the edit session and save the changes
#edit.stopEditing(True)

print ("Time it took to add rows: {}".format(daInsertEnd))
print ("ParcelPoints has been updated in SDE")


Record deleted: 127-078-14
Record deleted: 127-078-13
Record deleted: 123-272-20
Record deleted: 123-273-02
Record deleted: 123-271-14
Record deleted: 126-162-13
Record deleted: 127-072-05
Record deleted: 126-162-12
Record deleted: 127-078-12
Record deleted: 123-274-04
Record deleted: 123-273-04
Record deleted: 123-271-16
Record deleted: 130-192-13
Record deleted: 130-192-03
Record deleted: 130-192-10
Record deleted: 130-192-02
Record deleted: 130-192-08
Record deleted: 130-192-05
Record deleted: 132-053-19
Record deleted: 132-053-11
Record deleted: 132-053-18
Record deleted: 132-053-12
Record deleted: 132-053-16
Record deleted: 132-042-06
Record deleted: 126-162-11
Record deleted: 127-078-01
Record deleted: 126-162-14
Record deleted: 127-072-07
Record deleted: 127-078-11
Record deleted: 132-042-07
Record deleted: 127-530-23
Record deleted: 123-282-02
Record deleted: 123-282-08
Record deleted: 123-282-04
Record deleted: 123-282-03
Record deleted: 123-272-16
Record deleted: 127-530-19
R

Record deleted: 127-072-30
Record deleted: 127-072-06
Record deleted: 127-078-27
Record deleted: 127-078-29
Record deleted: 127-078-28
Record deleted: 126-172-04
Record deleted: 126-172-05
Record deleted: 127-490-01
Record deleted: 127-490-02
Record deleted: 126-172-06
Record deleted: 127-490-06
Record deleted: 127-490-07
Record deleted: 123-272-01
Record deleted: 123-051-03
Record deleted: 123-053-03
Record deleted: 123-053-04
Record deleted: 123-272-09
Record deleted: 132-221-05
Record deleted: 127-250-02
Record deleted: 122-530-35
Record deleted: 122-081-17
Record deleted: 122-081-16
Record deleted: 123-053-05
Record deleted: 123-271-17
Record deleted: 126-172-03
Record deleted: 127-490-03
Record deleted: 127-490-04
Record deleted: 126-172-07
Record deleted: 127-490-05
Record deleted: 126-172-12
Record deleted: 132-054-13
Record deleted: 132-054-15
Record deleted: 132-054-01
Record deleted: 132-053-22
Record deleted: 132-054-08
Record deleted: 132-054-06
Record deleted: 132-053-21
R

Record deleted: 126-292-58
Record deleted: 126-292-63
Record deleted: 123-162-13
Record deleted: 122-530-32
Record deleted: 132-211-26
Record deleted: 131-180-09
Record deleted: 124-340-27
Record deleted: 126-101-03
Record deleted: 126-140-00
Record deleted: 122-460-15
Record deleted: 123-138-07
Record deleted: 130-383-13
Record deleted: 124-340-40
Record deleted: 131-201-55
Record deleted: 124-032-21
Record deleted: 126-101-12
Record deleted: 126-101-10
Record deleted: 132-420-06
Record deleted: 127-600-03
Record deleted: 124-340-21
Record deleted: 122-052-22
Record deleted: 123-163-08
Record deleted: 131-261-40
Record deleted: 132-560-29
Record deleted: 122-060-22
Record deleted: 132-251-01
Record deleted: 122-126-22
Record deleted: 122-460-22
Record deleted: 124-340-41
Record deleted: 131-262-06
Record deleted: 122-125-02
Record deleted: 124-340-28
Record deleted: 122-121-09
Record deleted: 122-123-06
Record deleted: 131-270-09
Record deleted: 124-071-03
Record deleted: 125-482-10
R

Record deleted: 126-291-19
Record deleted: 124-063-02
Record deleted: 131-201-42
Record deleted: 123-271-09
Record deleted: 122-212-15
Record deleted: 127-420-29
Record deleted: 122-162-25
Record deleted: 127-420-32
Record deleted: 127-560-14
Record deleted: 127-420-35
Record deleted: 131-202-32
Record deleted: 125-141-34
Record deleted: 124-400-25
Record deleted: 125-544-13
Record deleted: 125-790-00
Record deleted: 131-121-18
Record deleted: 124-061-19
Record deleted: 125-141-01
Record deleted: 125-544-14
Record deleted: 124-500-32
Record deleted: 126-102-09
Record deleted: 126-082-03
Record deleted: 125-600-01
Record deleted: 131-070-36
Record deleted: 131-021-14
Record deleted: 124-081-03
Record deleted: 125-544-02
Record deleted: 131-460-02
Record deleted: 131-202-06
Record deleted: 126-521-05
Record deleted: 126-522-05
Record deleted: 124-072-04
Record deleted: 122-135-12
Record deleted: 124-031-01
Record deleted: 122-135-10
Record deleted: 124-064-06
Record deleted: 127-250-41
R

Record deleted: 131-023-01
Record deleted: 125-553-07
Record deleted: 129-252-02
Record deleted: 131-013-21
Record deleted: 131-040-07
Record deleted: 129-650-31
Record deleted: 125-163-18
Record deleted: 129-370-01
Record deleted: 125-541-11
Record deleted: 129-251-14
Record deleted: 125-161-30
Record deleted: 128-362-14
Record deleted: 128-361-13
Record deleted: 125-041-05
Record deleted: 128-132-06
Record deleted: 125-185-15
Record deleted: 125-373-16
Record deleted: 128-033-07
Record deleted: 128-033-03
Record deleted: 126-301-21
Record deleted: 125-541-04
Record deleted: 131-031-14
Record deleted: 129-251-10
Record deleted: 125-243-33
Record deleted: 126-251-19
Record deleted: 125-244-08
Record deleted: 126-302-14
Record deleted: 125-254-08
Record deleted: 128-280-01
Record deleted: 126-231-06
Record deleted: 125-564-12
Record deleted: 125-161-24
Record deleted: 125-562-07
Record deleted: 129-550-00
Record deleted: 125-564-20
Record deleted: 129-650-33
Record deleted: 125-162-07
R

...

Record added: 092-110-032
Record added: 092-010-009
Record added: 092-110-042
Record added: 092-010-010
Record added: 092-110-040
Record added: 116-100-036
Record added: 090-234-011
Record added: 116-090-054
Record added: 116-100-033
Record added: 116-120-022
Record added: 090-231-038
Record added: 116-090-038
Record added: 116-090-037
Record added: 116-010-019
Record added: 116-100-001
Record added: 090-232-033
Record added: 116-100-030
Record added: 090-231-011
Record added: 090-233-035
Record added: 116-090-007
Record added: 090-234-012
Record added: 090-232-022
Record added: 116-100-009
Record added: 116-090-036
Record added: 116-090-040
Record added: 116-090-035
Record added: 116-080-068
Record added: 116-090-041
Record added: 116-100-029
Record added: 116-090-039
Record added: 116-090-034
Record added: 090-231-010
Record added: 090-232-026
Record added: 090-232-027
Record added: 090-233-034
Record added: 090-233-030
Record added: 116-090-033
Record added: 116-080-059
Record added

Record added: 090-041-009
Record added: 112-190-033
Record added: 090-041-038
Record added: 092-170-043
Record added: 092-170-005
Record added: 092-170-006
Record added: 092-180-003
Record added: 092-180-031
Record added: 092-170-046
Record added: 092-180-004
Record added: 092-170-008
Record added: 092-180-001
Record added: 092-180-046
Record added: 092-180-006
Record added: 092-180-007
Record added: 092-180-008
Record added: 091-174-007
Record added: 091-186-001
Record added: 091-186-010
Record added: 091-172-018
Record added: 091-171-012
Record added: 091-172-001
Record added: 091-186-009
Record added: 091-174-006
Record added: 091-185-006
Record added: 091-172-017
Record added: 091-171-015
Record added: 091-186-008
Record added: 091-172-002
Record added: 091-184-005
Record added: 091-174-005
Record added: 115-070-002
Record added: 091-140-011
Record added: 115-070-001
Record added: 115-060-011
Record added: 115-060-021
Record added: 115-050-033
Record added: 090-321-006
Record added

Record added: 112-270-061
Record added: 111-270-065
Record added: 112-280-043
Record added: 111-270-017
Record added: 112-270-039
Record added: 111-270-058
Record added: 111-270-014
Record added: 112-280-002
Record added: 112-270-040
Record added: 110-060-069
Record added: 090-340-013
Record added: 111-120-024
Record added: 111-190-030
Record added: 112-240-034
Record added: 111-120-006
Record added: 111-190-011
Record added: 111-120-025
Record added: 111-110-038
Record added: 112-240-035
Record added: 111-120-026
Record added: 111-110-021
Record added: 111-120-005
Record added: 112-240-036
Record added: 111-110-042
Record added: 111-110-020
Record added: 111-190-031
Record added: 111-160-009
Record added: 111-150-030
Record added: 111-110-041
Record added: 111-190-010
Record added: 112-240-037
Record added: 111-120-004
Record added: 112-250-044
Record added: 111-110-019
Record added: 112-250-052
Record added: 111-110-018
Record added: 112-260-042
Record added: 111-110-040
Record added

Record added: 1318-23-310-050
Record added: 1319-19-720-010
Record added: 1318-24-701-010
Record added: 1319-19-310-042
Record added: 1318-23-310-038
Record added: 1318-23-710-081
Record added: 1319-19-310-013
Record added: 1318-23-311-019
Record added: 1319-19-714-018
Record added: 1318-23-310-039
Record added: 1319-19-714-016
Record added: 1319-19-717-013
Record added: 1318-23-710-069
Record added: 1318-24-702-005
Record added: 1318-24-301-007
Record added: 1319-19-717-010
Record added: 1319-19-717-012
Record added: 1319-19-717-011
Record added: 1318-24-711-006
Record added: 1318-23-311-020
Record added: 1319-19-802-002
Record added: 1319-19-310-016
Record added: 1318-24-301-006
Record added: 1318-24-311-014
Record added: 1318-24-711-016
Record added: 1318-24-301-005
Record added: 1319-19-720-009
Record added: 1318-24-404-001
Record added: 1318-23-810-063
Record added: 1318-23-810-053
Record added: 1318-22-002-047
Record added: 1318-23-410-069
Record added: 1318-23-810-028
Record add

Record added: 1319-19-720-016
Record added: 1318-23-310-032
Record added: 1318-23-710-083
Record added: 1319-19-310-011
Record added: 1318-24-311-009
Record added: 1318-23-312-002
Record added: 1319-19-310-041
Record added: 1319-19-720-002
Record added: 1318-23-310-029
Record added: 1319-19-718-008
Record added: 1319-19-310-040
Record added: 1319-19-310-033
Record added: 1318-23-710-012
Record added: 1319-19-720-018
Record added: 1318-23-710-030
Record added: 1318-24-710-014
Record added: 1319-19-310-039
Record added: 1318-23-314-001
Record added: 1319-19-717-006
Record added: 1318-24-801-010
Record added: 1318-23-811-021
Record added: 1318-22-002-065
Record added: 1319-19-411-017
Record added: 1318-23-810-100
Record added: 1318-22-002-050
Record added: 1318-23-410-039
Record added: 1318-22-002-040
Record added: 1318-23-810-085
Record added: 1318-22-002-068
Record added: 1318-23-810-064
Record added: 1318-23-410-053
Record added: 1318-23-811-033
Record added: 1318-23-410-004
Record add

### Update Parcel Base

In [5]:
import arcpy
from datetime import datetime

inputFC = r"C:/GIS/PROJECT/ParcelUpdate_Dev/Parcel_NewData.gdb/Parcel_Base"

outputFC = r"C:/GIS/PROJECT/SDE/SDE_Archive_2018.gdb/Parcels/Parcel_Base"

fields = ['APN', 'PPNO', 'JURISDICTION', 'PARCEL_ACRES', 'PARCEL_SQFT', 'SHAPE@XY']

# delete rows in sde feature class
daDeleteStart = datetime.now()

with arcpy.da.UpdateCursor(outputFC, fields) as dCursor:
    for row in dCursor:
        dCursor.deleteRow()
        
daDeleteEnd = datetime.now() - daDeleteStart
print ("Time it took to delete rows: {}".format(daDeleteEnd))

# insert rows from staging feature class into SDE feature class
daInsertStart = datetime.now()

with arcpy.da.InsertCursor(outputFC, fields) as iCursor:
    with arcpy.da.SearchCursor(inputFC, fields) as sCursor:
        for row in sCursor:
            iCursor.insertRow(row)

daInsertEnd = datetime.now() - daInsertStart
print ("Time it took to add rows: {}".format(daInsertEnd))
print ("ParcelPoints has been updated in SDE")

RuntimeError: cannot open 'C:/GIS/PROJECT/SDE/SDE_Archive_2018.gdb/Parcels/Parcel_Base'

### Update Parcel Master

In [ ]:
import arcpy
from datetime import datetime

inputFC = r"C:/GIS/PROJECT/ParcelUpdate_Dev/Parcel_NewData.gdb/Parcel_Master"

outputFC = r""

fields = ['APN', 'PPNO', 'JURISDICTION', 'PARCEL_ACRES', 'PARCEL_SQFT', 'SHAPE@XY']

# delete rows in sde feature class
daDeleteStart = datetime.now()

with arcpy.da.UpdateCursor(outputFC, fields) as dCursor:
    for row in dCursor:
        dCursor.deleteRow()
        
daDeleteEnd = datetime.now() - daDeleteStart
print ("Time it took to delete rows: {}".format(daDeleteEnd))

# insert rows from staging feature class into SDE feature class
daInsertStart = datetime.now()

with arcpy.da.InsertCursor(outputFC, fields) as iCursor:
    with arcpy.da.SearchCursor(inputFC, fields) as sCursor:
        for row in sCursor:
            iCursor.insertRow(row)

daInsertEnd = datetime.now() - daInsertStart
print ("Time it took to add rows: {}".format(daInsertEnd))
print ("Parcel_Master has been updated in SDE")

### Create Parcel Tables

In [5]:
table = r"F:\\GIS\\ParcelUpdate\\2018_10\\Workspace\\ParcelUpdate_Workspace.gdb\\Parcel_Master"
field_names = [field.name for field in arcpy.ListFields(table)]
# lists the index of the field names in parcel out data
for index, field in enumerate(field_names):
    print (index, field)

0 OBJECTID
1 Shape
2 APN
3 PPNO
4 HSE_NUMBR
5 UNIT_NUMBR
6 STR_DIR
7 STR_NAME
8 STR_SUFFIX
9 APO_ADDRESS
10 PSTL_TOWN
11 PSTL_STATE
12 PSTL_ZIP5
13 OWN_FIRST
14 OWN_LAST
15 OWN_FULL
16 MAIL_ADD1
17 MAIL_ADD2
18 MAIL_CITY
19 MAIL_STATE
20 MAIL_ZIP5
21 JURISDICTION
22 COUNTY
23 OWNERSHIP_TYPE
24 UNITS
25 COUNTY_LANDUSE
26 COUNTY_LANDUSE_DESCRIPTION
27 TRPA_LANDUSE_DESCRIPTION
28 REGIONAL_LANDUSE
29 SOIL_1974
30 SOIL_2003
31 ALLOWABLE_COVERAGE_BAILEY_SQFT
32 IMPERVIOUS_SURFACE_SQFT
33 HRA_NAME
34 WATERSHED_NUMBER
35 WATERSHED_NAME
36 PRIORITY_WATERSHED
37 BMP_STATUS
38 FIREPD
39 WITHIN_TRPA_BNDY
40 LITTORAL
41 AS_LANDVALUE
42 AS_IMPROVALUE
43 AS_SUM
44 TAX_LANDVALUE
45 TAX_IMPROVALUE
46 TAX_SUM
47 TAX_YEAR
48 PAS_ID
49 PAS_NAME
50 INDEX_1987
51 INDEX_1987_HYPERLINK
52 LOCAL_PLAN_HYPERLINK
53 ZONING
54 ZONING_DESCRIPTION
55 SINGLE_FAMILY_DENSITY
56 MULTI_FAMILY_DENSITY
57 TOURIST_ACCOMMODATION_DENSITY
58 BED_BREAKFAST_DENSITY
59 TIME_SHARE_DENSITY
60 COMMERCIAL_FLOOR_AREA_ALLOWED
61 SECOND

In [64]:
import arcpy

def getFieldMappings(fc_in, mapping_list):
    field_mappings = arcpy.FieldMappings()

    for in_field, out_field, out_type in mapping_list:
        field_map = arcpy.FieldMap()
        field_map.addInputField(fc_in, in_field)
        field = field_map.outputField
        field.name = out_field
        field.type = out_type
        field_map.outputField = field
        field_mappings.addFieldMap(field_map)
        print("added {} field map object".format(field.name))
        del field, field_map

    return field_mappings

# input table and output path
table = r"F:\GIS\ParcelUpdate\2018_10\Workspace\ParcelUpdate_Workspace.gdb\Parcel_Master"
outpath = r"F:\GIS\ParcelUpdate\2018_10\Workspace\ParcelUpdate_Workspace.gdb"

# list of all Parcel fields 
fieldListMaster = (
        "APN", "PPNO", "JURISDICTION", "HSE_NUMBR", "UNIT_NUMBR", "STR_DIR", "STR_NAME", "STR_SUFFIX", "APO_ADDRESS",
        "PSTL_TOWN", "PSTL_STATE", "PSTL_ZIP5", "OWN_FIRST", "OWN_LAST", "OWN_FULL", "MAIL_ADD1", "MAIL_ADD2", "MAIL_CITY",
        "MAIL_STATE", "MAIL_ZIP5", "AS_LANDVALUE", "AS_IMPROVALUE", "AS_SUM", "TAX_LANDVALUE", "TAX_IMPROVALUE", "TAX_SUM",
        "TAX_YEAR", "OWNERSHIP_TYPE", "TRPA_LANDUSE_DESCRIPTION", "COUNTY_LANDUSE", "COUNTY_LANDUSE_DESCRIPTION", "SOIL_1974",
        "SOIL_2003", "HRA_NAME", "WATERSHED_NUMBER", "WATERSHED_NAME",  "PRIORITY_WATERSHED", "PAS_ID", "PAS_NAME", "FIREPD",
        "BMP_STATUS", "WITHIN_TRPA_BNDY", "LITTORAL", "PARCEL_ACRES", "PARCEL_SQFT", "INDEX_1987",
        "INDEX_1987_HYPERLINK", "LOCAL_PLAN_HYPERLINK", "IMPERVIOUS_SURFACE_SQFT", "ALLOWABLE_COVERAGE_BAILEY_SQFT",
        "ZONING", "ZONING_DESCRIPTION", "SUBDISTRICT", "REGIONAL_LANDUSE", "SINGLE_FAMILY_DENSITY", "MULTI_FAMILY_DENSITY",
        "TOURIST_ACCOMMODATION_DENSITY", "BED_BREAKFAST_DENSITY", "TIME_SHARE_DENSITY", "COMMERCIAL_FLOOR_AREA_ALLOWED",
        "SECONDARY_DWELLING_UNIT_ALLOWED", "OVERLAY", "MAX_CP_RES_DENSITY", "MAX_CP_TAU_DENSITY", "SPECIAL_PLAN_AREA_OVERLAY",
        "TOWN_CENTER", "SPECIAL_AREA", "SPECIAL_PLANNING_DISTRICT", "SPECIAL_PLANNING_DISTRICT_TYPE", "LOCATION_TO_TOWNCENTER",
        "RETIRED")

#Export Parcel_Master table
table_out = "Parcel_Master_Table"

print ("Creating Field Map Objects for %s table" %(table_out))

if arcpy.Exists(outpath + "/" + table_out):
    arcpy.Delete_management(outpath + "/" + table_out)

master_dict = [(fieldListMaster[0], "APN", "Text"),
               (fieldListMaster[1], "PPNO", "Double"),
               (fieldListMaster[2], "JURISDICTION", "Text"),
               (fieldListMaster[3], "HSE_NUMBR", "Short Integer"),
               (fieldListMaster[4], "UNIT_NUMBR", "Text"),
               (fieldListMaster[5], "STR_DIR", "Text"),
               (fieldListMaster[6], "STR_NAME", "Text"),
               (fieldListMaster[7], "STR_SUFFIX", "Text"),
               (fieldListMaster[8], "APO_ADDRESS", "Text"),
               (fieldListMaster[9], "PSTL_TOWN", "Text"),
               (fieldListMaster[10], "PSTL_STATE", "Text"),
               (fieldListMaster[11], "PSTL_ZIP5", "Text"),
               (fieldListMaster[12], "OWN_FIRST", "Text"),
               (fieldListMaster[13], "OWN_LAST", "Text"),
               (fieldListMaster[14], "OWN_FULL", "Text"),
               (fieldListMaster[15], "MAIL_ADD1", "Text"),
               (fieldListMaster[16], "MAIL_ADD2", "Text"),
               (fieldListMaster[17], "MAIL_CITY", "Text"),
               (fieldListMaster[18], "MAIL_STATE", "Text"),
               (fieldListMaster[19], "MAIL_ZIP5", "Text"),
               (fieldListMaster[20], "AS_LANDVALUE", "Long"),
               (fieldListMaster[21], "AS_IMPROVALUE", "Long"),
               (fieldListMaster[22], "AS_SUM", "Long"),
               (fieldListMaster[23], "TAX_LANDVALUE", "Long"),
               (fieldListMaster[24], "TAX_IMPROVALUE", "Long"),
               (fieldListMaster[25], "TAX_SUM", "Long"),
               (fieldListMaster[26], "TAX_YEAR", "Text"),
               (fieldListMaster[27], "OWNERSHIP_TYPE", "Text"),
               (fieldListMaster[28], "TRPA_LANDUSE_DESCRIPTION", "Text"),
               (fieldListMaster[29], "COUNTY_LANDUSE", "Text"),
               (fieldListMaster[30], "COUNTY_LANDUSE_DESCRIPTION", "Text"),
               (fieldListMaster[31], "SOIL_1974", "Text"),
               (fieldListMaster[32], "SOIL_2003", "Text"),
               (fieldListMaster[33], "HRA_NAME", "Text"),
               (fieldListMaster[34], "WATERSHED_NUMBER", "Short"),
               (fieldListMaster[35], "WATERSHED_NAME", "Text"),
               (fieldListMaster[36], "PRIORITY_WATERSHED", "Text"),
               (fieldListMaster[37], "PAS_ID", "Text"),
               (fieldListMaster[38], "PAS_NAME", "Text"),
               (fieldListMaster[39], "FIREPD", "Text"),
               (fieldListMaster[40], "BMP_STATUS", "Text"),
               (fieldListMaster[41], "WITHIN_TRPA_BNDY", "Text"),
               (fieldListMaster[42], "LITTORAL", "Text"),
               (fieldListMaster[43], "PARCEL_ACRES", "Double"),
               (fieldListMaster[44], "PARCEL_SQFT", "Double"),
               (fieldListMaster[45], "INDEX_1987", "Text"),
               (fieldListMaster[46], "INDEX_1987_HYPERLINK", "Text"),
               (fieldListMaster[47], "LOCAL_PLAN_HYPERLINK", "Text"),
               (fieldListMaster[48], "IMPERVIOUS_SURFACE_SQFT", "Text"),
               (fieldListMaster[49], "ALLOWABLE_COVERAGE_BAILEY_SQFT", "Text"),
               (fieldListMaster[50], "ZONING", "Text"),
               (fieldListMaster[51], "ZONING_DESCRIPTION", "Text"),
               (fieldListMaster[53], "REGIONAL_LANDUSE", "Text"),
               (fieldListMaster[54], "SINGLE_FAMILY_DENSITY", "Text"),
               (fieldListMaster[55], "MULTI_FAMILY_DENSITY", "Text"),
               (fieldListMaster[56], "TOURIST_ACCOMMODATION_DENSITY", "Text"),
               (fieldListMaster[57], "BED_BREAKFAST_DENSITY", "Text"),
               (fieldListMaster[58], "TIME_SHARE_DENSITY", "Text"),
               (fieldListMaster[59], "COMMERCIAL_FLOOR_AREA_ALLOWED", "Text"),
               (fieldListMaster[60], "SECONDARY_DWELLING_UNIT_ALLOWED", "Text"),
               (fieldListMaster[61], "OVERLAY", "Text"),
               (fieldListMaster[62], "MAX_CP_RES_DENSITY", "Text"),
               (fieldListMaster[63], "MAX_CP_TAU_DENSITY", "Text"),
               (fieldListMaster[64], "SPECIAL_PLAN_AREA_OVERLAY", "Text"),
               (fieldListMaster[65], "TOWN_CENTER", "Text"),
               (fieldListMaster[66], "SPECIAL_AREA", "Text"),
               (fieldListMaster[67], "SPECIAL_PLANNING_DISTRICT", "Text"),
               (fieldListMaster[68], "SPECIAL_PLANNING_DISTRICT_TYPE", "Text"),
               (fieldListMaster[69], "LOCATION_TO_TOWNCENTER", "Text"),
               (fieldListMaster[70], "RETIRED", "Text")]

mapped = getFieldMappings(table, master_dict)

arcpy.TableToTable_conversion(table, outpath, table_out, "", mapped)

print ("Exported %s table" %(table_out))


#Export Parcel_Address Table
table_out = "Parcel_Address"

print ("Creating Field Map Objects for %s table" %(table_out))

if arcpy.Exists(outpath + "/" + table_out):
    arcpy.Delete_management(outpath + "/" + table_out)

address_dict = [(fieldListMaster[0], "APN", "Text"),
               (fieldListMaster[1], "PPNO", "Double"),
               (fieldListMaster[2], "JURISDICTION", "Text"),
               (fieldListMaster[3], "HSE_NUMBR", "Short Integer"),
               (fieldListMaster[4], "UNIT_NUMBR", "Text"),
               (fieldListMaster[5], "STR_DIR", "Text"),
               (fieldListMaster[6], "STR_NAME", "Text"),
               (fieldListMaster[7], "STR_SUFFIX", "Text"),
               (fieldListMaster[8], "APO_ADDRESS", "Text"),
               (fieldListMaster[9], "PSTL_TOWN", "Text"),
               (fieldListMaster[10], "PSTL_STATE", "Text"),
               (fieldListMaster[11], "PSTL_ZIP5", "Text")]

mapped = getFieldMappings(table, address_dict)

arcpy.TableToTable_conversion(table, outpath, table_out, "", mapped)

print ("Exported %s table" %(table_out))


#Export Parcel_Owner Table
table_out = "Parcel_Owner"

print ("Creating Field Map Objects for %s table" %(table_out))

if arcpy.Exists(outpath + "/" + table_out):
    arcpy.Delete_management(outpath + "/" + table_out)

owner_dict = [(fieldListMaster[0], "APN", "Text"),
               (fieldListMaster[1], "PPNO", "Double"),
               (fieldListMaster[2], "JURISDICTION", "Text"),
               (fieldListMaster[12], "OWN_FIRST", "Text"),
               (fieldListMaster[13], "OWN_LAST", "Text"),
               (fieldListMaster[14], "OWN_FULL", "Text"),
               (fieldListMaster[15], "MAIL_ADD1", "Text"),
               (fieldListMaster[16], "MAIL_ADD2", "Text"),
               (fieldListMaster[17], "MAIL_CITY", "Text"),
               (fieldListMaster[18], "MAIL_STATE", "Text"),
               (fieldListMaster[19], "MAIL_ZIP5", "Text")]

mapped = getFieldMappings(table, owner_dict)

arcpy.TableToTable_conversion(table, outpath, table_out, "", mapped)

print ("Exported %s table" %(table_out))


# Export Parcel_Value Table
table_out = "Parcel_Value"

print ("Creating Field Map Objects for %s table" %(table_out))

if arcpy.Exists(outpath + "/" + table_out):
    arcpy.Delete_management(outpath + "/" + table_out)

value_dict = [(fieldListMaster[0], "APN", "Text"),
               (fieldListMaster[1], "PPNO", "Double"),
               (fieldListMaster[2], "JURISDICTION", "Text"),
               (fieldListMaster[20], "AS_LANDVALUE", "Long"),
               (fieldListMaster[21], "AS_IMPROVALUE", "Long"),
               (fieldListMaster[22], "AS_SUM", "Long"),
               (fieldListMaster[23], "TAX_LANDVALUE", "Long"),
               (fieldListMaster[24], "TAX_IMPROVALUE", "Long"),
               (fieldListMaster[25], "TAX_SUM", "Long"),
               (fieldListMaster[26], "TAX_YEAR", "Text"),
               (fieldListMaster[9], "PSTL_TOWN", "Text"),
               (fieldListMaster[10], "PSTL_STATE", "Text"),
               (fieldListMaster[11], "PSTL_ZIP5", "Text"),
               (fieldListMaster[17], "MAIL_CITY", "Text"),
               (fieldListMaster[18], "MAIL_STATE", "Text"),
               (fieldListMaster[19], "MAIL_ZIP5", "Text"),
               (fieldListMaster[27], "OWNERSHIP_TYPE", "Text"),
               (fieldListMaster[43], "PARCEL_ACRES", "Double"),
               (fieldListMaster[44], "PARCEL_SQFT", "Double")]

mapped = getFieldMappings(table, value_dict)

arcpy.TableToTable_conversion(table, outpath, table_out, "", mapped)

print ("Exported %s table" %(table_out))


# Export Parcel_APO Table
table_out = "Parcel_APO"

print ("Creating Field Map Objects for %s table" %(table_out))

if arcpy.Exists(outpath + "/" + table_out):
    arcpy.Delete_management(outpath + "/" + table_out)

apo_dict = [(fieldListMaster[0], "APN", "Text"),
               (fieldListMaster[1], "PPNO", "Double"),
               (fieldListMaster[2], "JURISDICTION", "Text"),
               (fieldListMaster[14], "OWN_FULL", "Text"),
               (fieldListMaster[8], "APO_ADDRESS", "Text"),
               (fieldListMaster[27], "OWNERSHIP_TYPE", "Text"),
               (fieldListMaster[28], "TRPA_LANDUSE_DESCRIPTION", "Text"),
               (fieldListMaster[29], "COUNTY_LANDUSE", "Text"),
               (fieldListMaster[30], "COUNTY_LANDUSE_DESCRIPTION", "Text"),
               (fieldListMaster[31], "SOIL_1974", "Text"),
               (fieldListMaster[32], "SOIL_2003", "Text"),
               (fieldListMaster[33], "HRA_NAME", "Text"),
               (fieldListMaster[34], "WATERSHED_NUMBER", "Short"),
               (fieldListMaster[35], "WATERSHED_NAME", "Text"),
               (fieldListMaster[36], "PRIORITY_WATERSHED", "Text"),
               (fieldListMaster[37], "PAS_ID", "Text"),
               (fieldListMaster[38], "PAS_NAME", "Text"),
               (fieldListMaster[39], "FIREPD", "Text"),
               (fieldListMaster[41], "WITHIN_TRPA_BNDY", "Text"),
               (fieldListMaster[42], "LITTORAL", "Text"),
               (fieldListMaster[43], "PARCEL_ACRES", "Double"),
               (fieldListMaster[44], "PARCEL_SQFT", "Double"),]

mapped = getFieldMappings(table, apo_dict)

arcpy.TableToTable_conversion(table, outpath, table_out, "", mapped)

print ("Exported %s table" %(table_out))


Creating Field Map Objects for Parcel_Master_Table table
added APN field map object
added PPNO field map object
added JURISDICTION field map object
added HSE_NUMBR field map object
added UNIT_NUMBR field map object
added STR_DIR field map object
added STR_NAME field map object
added STR_SUFFIX field map object
added APO_ADDRESS field map object
added PSTL_TOWN field map object
added PSTL_STATE field map object
added PSTL_ZIP5 field map object
added OWN_FIRST field map object
added OWN_LAST field map object
added OWN_FULL field map object
added MAIL_ADD1 field map object
added MAIL_ADD2 field map object
added MAIL_CITY field map object
added MAIL_STATE field map object
added MAIL_ZIP5 field map object
added AS_LANDVALUE field map object
added AS_IMPROVALUE field map object
added AS_SUM field map object
added TAX_LANDVALUE field map object
added TAX_IMPROVALUE field map object
added TAX_SUM field map object
added TAX_YEAR field map object
added OWNERSHIP_TYPE field map object
added TRPA_

## TO DO
### Fix Unit field for Placer, El Dorado and Douglas
### Add Land Use Calculation NOT OWNERSHIP_TYPE = 'PRIVATE' AND TRPA_LANDUSE_DESCRIPTION = 'Vacant' 
### Fix Duplicates at the beginning of the script

## References

#### Accessing data using cursors
#### http://pro.arcgis.com/en/pro-app/arcpy/get-started/data-access-using-cursors.htm

#### Replacement for the field calculator
#### https://gis.stackexchange.com/questions/177923/using-updatecursor-for-joined-field-in-arcpy/178168#178168
#### https://community.esri.com/blogs/richard_fairhurst/2014/11/08/turbo-charging-data-manipulation-with-python-cursors-and-dictionaries

#### Which way is faster?
#### https://gis.stackexchange.com/questions/195197/which-is-the-faster-way-to-copy-data-to-another-feature-class-feature-class-to?utm_medium=organic&utm_source=google_rich_qa&utm_campaign=google_rich_qa

#### Full Address Calculation
#### https://community.esri.com/thread/42173
#### https://bit.ly/2HsQL9x

#### How to create the attribute join and update function:
##### https://gis.stackexchange.com/questions/177923/using-updatecursor-for-joined-field-in-arcpy/178168?utm_medium=organic&utm_source=google_rich_qa&utm_campaign=google_rich_qa

#### How to create the centroid feature layer:
##### http://pro.arcgis.com/en/pro-app/arcpy/data-access/featureclasstonumpyarray.htm
##### http://pro.arcgis.com/en/pro-app/arcpy/data-access/numpyarraytofeatureclass.htm

#### How to use the Spatial Join tool:
##### http://pro.arcgis.com/en/pro-app/tool-reference/analysis/spatial-join.htm

#### How to use the Select by Location tool:
##### http://desktop.arcgis.com/en/arcmap/10.3/tools/data-management-toolbox/select-layer-by-location.htm

#### How to use the Calculate field tool:
##### http://pro.arcgis.com/en/pro-app/tool-reference/data-management/calculate-field.htm

